In [3]:
import numpy as np
import Plot as plot
import math
import matplotlib.pyplot as plt
import plotly
import plotly.plotly as py
import plotly.graph_objs as go
import plotly.offline as offline
import time
import datetime
import pickle
import os
import scipy.spatial
from scipy.spatial import distance
from sklearn.metrics.pairwise import euclidean_distances
import matplotlib as plt
import logging
from scipy import signal
import learningAlgs as classImportLA
import dataManipulation as dataMan
from itertools import permutations
import importlib
from datetime import timedelta
from multiprocessing import Pool
import multiprocessing
import pandas as pd
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import mean_squared_error
from sklearn.naive_bayes import GaussianNB
from sklearn.neural_network import MLPClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import KFold
from sklearn.metrics import f1_score
from sklearn.metrics import accuracy_score
from sklearn.metrics import precision_score
from sklearn.metrics import recall_score
from sklearn.cluster import KMeans
import timeIntervalPlotter as intervalPlotter
import pysal
import warnings
import lumping_traditional as oldLumping
import boundaryFull_SS_WeightedLumping as WLumping
from importlib import reload
from scipy.stats import rayleigh
import dataManipulation as dataMan
import matplotlib.pyplot as plt
import processData as processData
import tensorflow as tf
import tensorflow_probability as tfp
from random import shuffle
warnings.filterwarnings('always')
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)


In [4]:
import platform
print(platform.python_version())

3.6.8


In [35]:
import pkg_resources
pkg_resources.get_distribution("tensorflow").version

'1.15.0'

In [222]:
def classifying(CU, boundaries):
    occupiedBandwidth = (CU / 255) * 100
    for i in range(len(boundaries)):
        if occupiedBandwidth <= boundaries[i]:
            return i

def simpleLogisticRegression(data, timeIndexes, minuteSplit, boundaries):
    warnings.filterwarnings('always')
    reg = "l2"
    solvers = "lbfgs"
    clf = LogisticRegression(penalty = reg, max_iter = 100000, random_state = 0,
                             solver = solvers , multi_class = 'multinomial')
    accuracyValue = 0
    numOfElements = 0
    f1scoreValue = 0
    precisionValue = 0
    recallValue = 0
    prevRowTrain = np.inf
    prevCU = np.inf

    sampleIntervals = 6 #seconds
    minuteSplit = 30 #minutes
    numOfSamples = minuteSplit * 60 / sampleIntervals
    # numberOfDays = len(numOfDays)
    days = np.zeros(7)
    numOfThirtyMinsPerDay = np.zeros(int((24 * 60) / minuteSplit)) #in this case 48
#     which6SecondsPerPeriod = np.zeros(int(minuteSplit * 60 / sampleIntervals)) #in this case 300
    prevRowTrain = np.inf
    prevCU = np.inf

    XArraysForLearning = []
    YArraysForLearning = []
    XArraysForTesting = []
    YArraysForTesting = []

    x = timeIndexes
    iterPandas = data.loc[(data["timeIndex"] == x)].copy()

    iterPandas = iterPandas.sample(frac = 1)

    trainingDataFrame = iterPandas.iloc[:int(np.floor(0.8 * len(iterPandas)))].copy()

    trainingDataFrame["cuClass"] = trainingDataFrame["CU"].apply(lambda x: classifying(x, boundaries))

    stackCounter = 0
    prevCU = 0
    print("start training set generation")
    numberOfFeatures = len(boundaries) + 12 + 5  + 1 #month and correlations and logDiff
    XArraysForLearning = np.zeros(shape=(len(trainingDataFrame), numberOfFeatures))
    YArraysForLearning = np.zeros(shape=(len(trainingDataFrame), len(boundaries)))
    print(len(trainingDataFrame))
    counter = 0
    pandasIndexCounter = 0
    for index, row in trainingDataFrame.iterrows():
        month = int(row["month"])
        XArraysForLearning[pandasIndexCounter, prevCU] = 1
        XArraysForLearning[pandasIndexCounter, len(boundaries) + month] = 1
        for corrs in range(5):
            XArraysForLearning[pandasIndexCounter, len(boundaries) + 12 + corrs] = row["corr" + str(corrs + 1)]
        YArraysForLearning[pandasIndexCounter, row["cuClass"]] = 1

        which6SecondsPerPeriod = 0
        prevCU = row["cuClass"]
        pandasIndexCounter += 1


    weights = np.random.randn(XArraysForLearning.shape[1])
    print("Testing")
    #********************LR testing********************


    testingDataFrame = iterPandas.iloc[int(np.floor(0.8 * len(iterPandas))):].copy()

    testingDataFrame["cuClass"] = testingDataFrame["CU"].apply(lambda x: classifying(x, boundaries))


    stackCounter = 0
    prevCU = 0
    which6SecondsPerPeriod = np.zeros(int(minuteSplit * 60 / sampleIntervals)) #in this case 300

#     numberOfFeatures = len(boundaries) + len(which6SecondsPerPeriod)
    XArraysForTesting = np.zeros(shape=(len(testingDataFrame), numberOfFeatures))
    YArraysForTesting = np.zeros(shape=(len(testingDataFrame), len(boundaries)))

    counter = 0
    pandasIndexCounter = 0
    print("length of test is: ", len(testingDataFrame))
    for index, row in testingDataFrame.iterrows():
        month = int(row["month"])
        XArraysForTesting[pandasIndexCounter, prevCU] = 1
        XArraysForTesting[pandasIndexCounter, len(boundaries) + month] = 1
        for corrs in range(5):        
            XArraysForTesting[pandasIndexCounter, len(boundaries) + 12 + corrs] = row["corr" + str(corrs + 1)]
        YArraysForTesting[pandasIndexCounter, row["cuClass"]] = 1

        which6SecondsPerPeriod = 0
        prevCU = row["cuClass"]
        pandasIndexCounter += 1


    # print(XArraysForLearning.shape)
    # print(YArraysForLearning.shape)

    return XArraysForLearning, YArraysForLearning, XArraysForTesting, YArraysForTesting, boundaries


def tensorFlowLossNN(w, XArraysForLearning, YArraysForLearning, XArraysForTesting, YArraysForTesting, boundaries):
    batch_size = 64
    learning_rate = 0.001
    numOfEpochs = 200
    graph = tf.Graph()
    n_hidden_1 = YArraysForLearning.shape[1] # 1st layer number of neurons
    n_hidden_2 = YArraysForLearning.shape[1]

    with graph.as_default():
        x = tf.placeholder(tf.float32, shape = (batch_size, XArraysForLearning.shape[1]))
        y_ = tf.placeholder(tf.float32, shape = (batch_size, YArraysForLearning.shape[1]))
        W = tf.Variable(tf.truncated_normal([XArraysForLearning.shape[1], YArraysForLearning.shape[1]]), name="weights", dtype=tf.float32)
        b = tf.Variable(tf.truncated_normal([YArraysForLearning.shape[1]]), dtype=tf.float32)
        
#         w = w.astype("float32")
#         weight = np.vstack((w,w))
#         for i in range(YArraysForLearning.shape[1] - 2):
#             weight = np.vstack((weight, w))
        
        weights = {
            'h1': tf.Variable(tf.random_normal([XArraysForLearning.shape[1], n_hidden_1])),
            'h2': tf.Variable(tf.random_normal([n_hidden_1, n_hidden_2]), dtype = tf.float32),
            'out': tf.Variable(tf.random_normal([n_hidden_2, YArraysForLearning.shape[1]]))
        }
        print(weights["h2"])
        biases = {
            'b1': tf.Variable(tf.random_normal([n_hidden_1])),
            'b2': tf.Variable(tf.random_normal([n_hidden_2])),
            'out': tf.Variable(tf.random_normal([YArraysForLearning.shape[1]]))
        }

        layer_1 = tf.add(tf.matmul(x, weights['h1']), biases['b1'])
        logits = tf.add(tf.matmul(layer_1, weights['h2']), biases['b2'])
#         logits = tf.matmul(layer_2, weights['out']) + biases['out']

        tf_test_dataset64 = tf.constant(XArraysForTesting)
        tf_test_dataset = tf.cast(tf_test_dataset64, tf.float32)


        beta = 0.05
        # logits = tf.matmul(x, W)
        train_prediction = tf.nn.softmax(logits)
        # train_prediction = tf.nn.softmax_cross_entropy_with_logits_v2(labels = y_, logits = logits)
        test_prediction = tf.nn.softmax(tf.matmul(tf.matmul(tf_test_dataset, weights["h1"]) + biases["b1"], weights["h2"]) + biases["b2"])

        # x = XArraysForLearning[0:(0 + batch_size), :]
        # y_ = tf.Variable(YArraysForLearning[0:(0 + batch_size), :])

        # loss = assymetricLossFunction(train_prediction, y_, boundaries)
        # loss = assymetricLossFunction(train_prediction, y_, boundaries)
        loss = tf.nn.softmax_cross_entropy_with_logits_v2(logits = logits, labels = y_)
        # regularizer = tf.nn.l2_loss(W)
        # loss = tf.reduce_mean(loss + beta * regularizer)
        # loss = tf.nn.softmax_cross_entropy_with_logits_v2(logits = train_prediction, labels = y_)
        optimizer = tf.train.AdamOptimizer(learning_rate).minimize(loss)

        prevAcc = 0

    with tf.Session(graph=graph) as session:
        tf.global_variables_initializer().run()
        print(weights["h2"].eval())
        print("Initialized")

        numberOfBatchIteration = int(XArraysForLearning.shape[0] / batch_size)
        restOfData = XArraysForLearning.shape[0] % batch_size
        if restOfData != 0:
            numberOfBatchIteration += 1

        accuracy_earlyStop = 0
        earlyStoppingCounter = 0
        prevW = W
        for epoch in range(numOfEpochs):
            accuracyValue = 0
            lossValue = 0
            totalBatch = 0
            i = 0
            randomize = np.arange(XArraysForLearning.shape[0])
            np.random.shuffle(randomize)
            XArraysForLearning = XArraysForLearning[randomize]
            YArraysForLearning = YArraysForLearning[randomize]

            for iteration in range(numberOfBatchIteration):
                if (iteration == numberOfBatchIteration - 1) and restOfData != 0:
                    break
                    batch_data = XArraysForLearning[i:, :]
                    batch_labels = YArraysForLearning[i:, :]

                else:
                    batch_data = XArraysForLearning[i:(i + batch_size), :]
                    batch_labels = YArraysForLearning[i:(i + batch_size), :]

                    i += batch_size


                feed_dict = {x : batch_data, y_ : batch_labels}
                _, predictions, l = session.run([optimizer, train_prediction, loss], feed_dict=feed_dict)

                lossValue = (np.sum(l))
                totalBatch += batch_size
                # print(accuracy(batch_data, batch_labels))
                accuracyValue += accuracy(predictions, batch_labels) * batch_size
                # if accuracy(test_prediction.eval(), YArraysForTesting) < prevAcc and earlyStoppingCounter == 400:
                #     print(prevAcc)
                #     break
                #
                # elif accuracy(test_prediction.eval(), YArraysForTesting) < prevAcc:
                #     earlyStoppingCounter += 1
                #
                # elif accuracy(test_prediction.eval(), YArraysForTesting) >= prevAcc:
                #     earlyStoppingCounter = 0

            # print("Minibatch step {0}".format(step))
            # print("training Acc is: {:.3f}".format(accuracy(predictions,batch_labels)))
            # prevAcc = accuracy(test_prediction.eval(), YArraysForTesting)
            print("for epoch and loss:", epoch, np.mean(l))
            totalAccuracy = accuracyValue/totalBatch
            print(accuracyValue/totalBatch)
            if accuracy(test_prediction.eval(), YArraysForTesting) > accuracy_earlyStop:
                accuracy_earlyStop = accuracy(test_prediction.eval(), YArraysForTesting)

            else:
                earlyStoppingCounter += 1

            if earlyStoppingCounter == 50:
                break



        # print(session.run(W))
        predictionResult = test_prediction.eval()
        accResult = accuracy(predictionResult , YArraysForTesting)
        print("Penalty Value: {:.3f}".format(assymetricPredictionScore(predictionResult, YArraysForTesting, boundaries)))
        if accuracy_earlyStop > accResult:
            print("accuracy Result is: ", accuracy_earlyStop)
        else:
            print("accuracy Result is: ", accResult)
        print(weights["h2"].eval())

            
def assymetricLossFunction(prediction, correctLable, boundaries):
    sess = tf.Session()
    xAxisPoints = np.linspace(rayleigh.ppf(0.01), rayleigh.ppf(0.99), 338)
    #number of overal datapoints must stay the same all the time
    maxState = 338
    inverseDistrib = max(rayleigh.pdf(xAxisPoints)) - rayleigh.pdf(xAxisPoints)
    inverseDistrib = tf.constant(inverseDistrib)
    xAxisPoints -= xAxisPoints[np.argmin(inverseDistrib)]
    minState = np.argmin(inverseDistrib)
    numberOfOverUtilizedStates = maxState - minState
    numberOfUnderUtilizedStates = minState
    minState = tf.constant(minState, tf.float32)
    numberOfOverUtilizedStates = tf.constant(numberOfOverUtilizedStates, tf.float32)
    numberOfUnderUtilizedStates = tf.constant(numberOfUnderUtilizedStates, tf.float32)

    underUtilVal = numberOfUnderUtilizedStates / 100
    overUtilVal = numberOfOverUtilizedStates / 100


    boundaries = tf.constant(boundaries, tf.float32)
    correctLableIndex = tf.argmax(correctLable, 1)

    diffPercentage = []
    for index in range(correctLableIndex.shape[0]):
        diffPercentage.append(boundaries[correctLableIndex[index]] - boundaries[:])

    diffPercentage = tf.stack(diffPercentage)

    penalties = []

    counter = 0
    for i in range(diffPercentage.shape[0]):
        for j in range(diffPercentage.shape[1]):
            counter += 1

            penalties.append(tf.cond(
                    tf.greater(diffPercentage[i][j], 0),
                    lambda: inverseDistrib[tf.dtypes.cast(minState + tf.math.floor
                                                                   (tf.math.scalar_mul(diffPercentage[i][j],
                                                                                       overUtilVal)), tf.int32)],
                    lambda: inverseDistrib[tf.dtypes.cast(minState + tf.math.floor
                                                                   (tf.math.scalar_mul
                                                                    (diffPercentage[i][j], underUtilVal))
                                                                   , tf.int32)]
                    ))

    penalties = tf.stack(penalties)
    penalties = tf.dtypes.cast(penalties, tf.float32)
    penalties = tf.reshape(penalties, diffPercentage.shape)
    penalties = penalties / tf.norm(penalties)

    # weights = tf.reduce_sum(penalties * (1-prediction), axis=1)
    weights = (1 - penalties) * prediction
    weights = weights / tf.norm(weights)
    # print(correctLable)
    # print(prediction)
    # print(penalties)
    loss = tf.losses.softmax_cross_entropy(onehot_labels = correctLable, logits = weights)
    # weighted_losses = tf.nn.softmax_cross_entropy_with_logits_v2(labels = penalties, logits = prediction)
    # loss = tf.reduce_sum(weighted_losses)
    # loss = tf.reduce_sum(penalties * prediction)
    return tf.reduce_mean(loss)

def assymetricPredictionScore(predictedLables, trueLables, boundaries):
    xAxisPoints = np.linspace(rayleigh.ppf(0.01), rayleigh.ppf(0.99), 338)
    #number of overal datapoints must stay the same all the time
    maxState = 338

    inverseDistrib = max(rayleigh.pdf(xAxisPoints)) - rayleigh.pdf(xAxisPoints)
    minState = np.argmin(inverseDistrib)

    underUtilizedSum = 0
    overUtilizedSum = 0
    numberOfUnderUtilizedStates = minState - 0
    numberOfOverUtilizedStates = maxState - minState

    xAxisPoints -= xAxisPoints[np.argmin(inverseDistrib)]

    underUtilVal = numberOfUnderUtilizedStates / 100
    overUtilVal = numberOfOverUtilizedStates / 100

    correctLableIndex = np.argmax(trueLables, 1)
    predictionIndex = np.argmax(predictedLables, 1)

    diffPercentage = np.zeros(shape = (predictedLables.shape))

    penalties = np.zeros(shape = (predictedLables.shape))

    for index in range(predictedLables.shape[0]):
        diffPercentage[index] = boundaries[correctLableIndex[index]] - boundaries[:]


    for i in range(diffPercentage.shape[0]):
        for j in range(diffPercentage.shape[1]):
            if diffPercentage[i][j] > 0:
                penalties[i][j] = inverseDistrib[minState + math.floor
                                                  (diffPercentage[i][j] * overUtilVal)]
            else:
                penalties[i][j] = inverseDistrib[minState + math.floor
                                                  (diffPercentage[i][j] * underUtilVal)]

    sumOfPenalty = 0
    for i in range(predictionIndex.shape[0]):
        penalties[i] = penalties[i] / np.sum(penalties[i])
        sumOfPenalty += penalties[i][predictionIndex[i]]

    return sumOfPenalty

def accuracy(predictedLables, trueLables):
    import sys
    np.set_printoptions(threshold=sys.maxsize)
    correctLableIndex = np.argmax(trueLables, 1)
    predictionIndex = np.argmax(predictedLables, 1)
    errors = [0 for i in range(trueLables.shape[1])]
    corrects = [0 for i in range(trueLables.shape[1])]
    for i in range(len(correctLableIndex)):
        if correctLableIndex[i] != predictionIndex[i]:
            errors[correctLableIndex[i]] += 1
            corrects[predictionIndex[i]] += 1
#     print("errors: ", errors)
#     print("corrects: ", corrects)
    acc = np.float64(np.sum(correctLableIndex == predictionIndex)/predictedLables.shape[0])
    # wrongPred = np.where(predictionIndex != correctLableIndex)
    # print(predictionIndex[wrongPred])
    # print(correctLableIndex[wrongPred])
    return acc
            

In [37]:
def bandwidthPercentage(vectorMatrix):
    percentageIncreament = (100 / vectorMatrix.shape[0])
    percentageMatrix = []
    maxPercentage = 0
    for j in range(vectorMatrix.shape[0]):
        maxPercentage += percentageIncreament
        percentageMatrix.append([[j], maxPercentage, False])

    return percentageMatrix

def reduceMatrixAllInOne(transitionMatrix):
    reload(oldLumping)
    percentageMatrix_list = bandwidthPercentage(transitionMatrix)
    zero_cols_rows = []
    #*************removing zeros from columns and rows (matrix reduction) ****************
    for i in range(len(transitionMatrix)):
        if (np.sum(transitionMatrix[i]) == 0) and (np.sum(transitionMatrix[:,i]) == 0):
            zero_cols_rows.append(i)


    irreducible_matrix = transitionMatrix.copy()
    for i in range(len(zero_cols_rows) - 1, -1, -1):
        irreducible_matrix = np.delete(irreducible_matrix, zero_cols_rows[i], axis = 0)
        irreducible_matrix = np.delete(irreducible_matrix, zero_cols_rows[i], axis = 1)
        percentageMatrix_list[zero_cols_rows[i]][2] = True


    for i in range(len(percentageMatrix_list) - 1, 0, -1):
        if (percentageMatrix_list[i][2] == True) and (percentageMatrix_list[i - 1][2] == True):
            percentageMatrix_list[i - 1][0].extend(percentageMatrix_list[i][0])
            percentageMatrix_list[i - 1][1] = percentageMatrix_list[i][1]
            del percentageMatrix_list[i]

    result = oldLumping.lumping(irreducible_matrix, percentageMatrix_list, False)



def preparingMatrixForLumping(transitionMatrix):
    reload(oldLumping)
    percentageMatrix_list = bandwidthPercentage(transitionMatrix)
    zero_cols_rows = []
    #*************removing zeros from columns and rows (matrix reduction) ****************
    for i in range(len(transitionMatrix)):
        if (np.sum(transitionMatrix[i]) == 0) and (np.sum(transitionMatrix[:,i]) == 0):
            zero_cols_rows.append(i)


    irreducible_matrix = transitionMatrix.copy()
    for i in range(len(zero_cols_rows) - 1, -1, -1):
        irreducible_matrix = np.delete(irreducible_matrix, zero_cols_rows[i], axis = 0)
        irreducible_matrix = np.delete(irreducible_matrix, zero_cols_rows[i], axis = 1)
        percentageMatrix_list[zero_cols_rows[i]][2] = True


    for i in range(len(percentageMatrix_list) - 1, 0, -1):
        if (percentageMatrix_list[i][2] == True) and (percentageMatrix_list[i - 1][2] == True):
            percentageMatrix_list[i - 1][0].extend(percentageMatrix_list[i][0])
            percentageMatrix_list[i - 1][1] = percentageMatrix_list[i][1]
            del percentageMatrix_list[i]

    for i in range(len(irreducible_matrix)):
        if np.sum(irreducible_matrix[i], dtype = np.float32) != 1.0:
            print(np.sum(irreducible_matrix[i], dtype = np.float32))

    return percentageMatrix_list, irreducible_matrix

def lumpingStatesOneByOne(percentageMatrix_list, irreducible_matrix):

    # savedResult = 0
    result = oldLumping.lumping(irreducible_matrix, percentageMatrix_list, True)

    min_degree, min_error, irreducible_matrix, best_sectors = result[0], result[1], result[2], result[3]

    zero_cols_rows = []
    for i in range(len(irreducible_matrix)):
        if (np.sum(irreducible_matrix[i]) == 0) and (np.sum(irreducible_matrix[:,i]) == 0):
            zero_cols_rows.append(i)

    if len(zero_cols_rows) != 0:
        for i in range(len(zero_cols_rows) - 1, -1, -1):
            irreducible_matrix = np.delete(irreducible_matrix, zero_cols_rows[i], axis = 0)
            irreducible_matrix = np.delete(irreducible_matrix, zero_cols_rows[i], axis = 1)

        percentageMatrix_list = reduceMatrix(percentageMatrix_list, zero_cols_rows)

    print("length of best lumped is: ", len(irreducible_matrix))

    percentageMatrix_list = mergeStates(best_sectors, percentageMatrix_list)

    for i in range(len(irreducible_matrix)):
        if (np.sum(irreducible_matrix[i], dtype = np.float32) != 1.0):

            print(i, np.sum(irreducible_matrix[i], dtype = np.float32))

    for i in range(irreducible_matrix.shape[0]):
        sum = 0
        sum = np.sum(irreducible_matrix[i])
        if sum != 0:
            irreducible_matrix[i] = irreducible_matrix[i]/sum

    for i in range(len(irreducible_matrix)):
        if (np.sum(irreducible_matrix[i], dtype = np.float32) != 1.0):

            print(i, np.sum(irreducible_matrix[i], dtype = np.float32))

    count = 0
    for i in range(len(percentageMatrix_list)):
        if percentageMatrix_list[i][2] == False:
            count += 1
    print("percentageMatrix length is: ", count)

    return(percentageMatrix_list, irreducible_matrix)

    # if len(irreducible_matrix) == 26:
        # break
    # result = oldLumping.lumping(irreducible_matrix, percentageMatrix_list, False)
    # return result

def reduceMatrix(percentageMatrix, zero_cols_rows):
    index_in_percentage_matrix = np.inf
    counter = 0
    for x in range(len(zero_cols_rows)):
        for i in range(len(percentageMatrix)):
            if percentageMatrix[i][2] == False:
                if zero_cols_rows[x] == counter:
                    index_in_percentage_matrix = i
                    break
                counter += 1
        percentageMatrix[index_in_percentage_matrix][2] = True
        if index_in_percentage_matrix == (len(percentageMatrix) - 1):
            if percentageMatrix[index_in_percentage_matrix - 1][2] == True:
                percentageMatrix[index_in_percentage_matrix - 1][0].extend(
                    percentageMatrix[index_in_percentage_matrix][0])

                percentageMatrix[index_in_percentage_matrix - 1][1] = percentageMatrix[index_in_percentage_matrix][1]
                del percentageMatrix[index_in_percentage_matrix]

        elif index_in_percentage_matrix == 0:
            if percentageMatrix[index_in_percentage_matrix + 1][2] == True:
                percentageMatrix[index_in_percentage_matrix][0].extend(
                    percentageMatrix[index_in_percentage_matrix + 1][0])

                percentageMatrix[index_in_percentage_matrix][1] = percentageMatrix[index_in_percentage_matrix + 1][1]
                del percentageMatrix[index_in_percentage_matrix + 1]

        else:
            if (percentageMatrix[index_in_percentage_matrix - 1][2] == True) and (
                percentageMatrix[index_in_percentage_matrix + 1][2] == True):
                leftside_bandwidth_val = 0
                rightside_bandwidth_val = 0
                if (index_in_percentage_matrix - 1) != 0:
                    leftside_bandwidth_val = percentageMatrix[index_in_percentage_matrix][1] - percentageMatrix[index_in_percentage_matrix - 2][1]
                else:
                    leftside_bandwidth_val = percentageMatrix[index_in_percentage_matrix][1]
                rightside_bandwidth_val = percentageMatrix[index_in_percentage_matrix + 1][1] - percentageMatrix[index_in_percentage_matrix - 1][1]

                if leftside_bandwidth_val <= rightside_bandwidth_val:
                    percentageMatrix[index_in_percentage_matrix - 1][0].extend(
                        percentageMatrix[index_in_percentage_matrix][0])

                    percentageMatrix[index_in_percentage_matrix - 1][1] = percentageMatrix[index_in_percentage_matrix][1]
                    del percentageMatrix[index_in_percentage_matrix]

                else:
                    percentageMatrix[index_in_percentage_matrix][0].extend(
                        percentageMatrix[index_in_percentage_matrix + 1][0])

                    percentageMatrix[index_in_percentage_matrix][1] = percentageMatrix[index_in_percentage_matrix + 1][1]
                    del percentageMatrix[index_in_percentage_matrix + 1]

            elif (percentageMatrix[index_in_percentage_matrix - 1][2] == True) and (
                percentageMatrix[index_in_percentage_matrix + 1][2] == False):

                percentageMatrix[index_in_percentage_matrix - 1][0].extend(
                    percentageMatrix[index_in_percentage_matrix][0])

                percentageMatrix[index_in_percentage_matrix - 1][1] = percentageMatrix[index_in_percentage_matrix][1]
                del percentageMatrix[index_in_percentage_matrix]

            elif (percentageMatrix[index_in_percentage_matrix - 1][2] == False) and (
                percentageMatrix[index_in_percentage_matrix + 1][2] == True):

                percentageMatrix[index_in_percentage_matrix][0].extend(
                    percentageMatrix[index_in_percentage_matrix + 1][0])

                percentageMatrix[index_in_percentage_matrix][1] = percentageMatrix[index_in_percentage_matrix + 1][1]
                del percentageMatrix[index_in_percentage_matrix + 1]

    return percentageMatrix




def mergeStates(best_sectors, percentageMatrix):
    False_state_in_percentageMatrix = np.inf
    for i in range(1, len(best_sectors)):
        if best_sectors[i] - best_sectors[i - 1] == 2:
            False_state_in_percentageMatrix = best_sectors[i]
            #it means states number (whole_subset[i] - 1) and (whole_subset[i] - 2) should merge
            #it is also the (whole_subset[i]) False and (whole_subset[i] - 1) False in percentageMatrix
            break

    index1_in_percentage_matrix = np.inf
    index2_in_percentage_matrix = np.inf
    counter = 0
    for i in range(len(percentageMatrix)):
        if percentageMatrix[i][2] == False:
            counter += 1
            if counter == (False_state_in_percentageMatrix - 1):
                index1_in_percentage_matrix = i
            elif counter == False_state_in_percentageMatrix:
                index2_in_percentage_matrix = i
                break

    # print("indices are: ", index1_in_percentage_matrix, index2_in_percentage_matrix)
    # print("values of indices: ", percentageMatrix[index1_in_percentage_matrix])
    # print("values of indices: ", percentageMatrix[index2_in_percentage_matrix])
    if (index2_in_percentage_matrix) == (index1_in_percentage_matrix + 1):
        percentageMatrix[index1_in_percentage_matrix][0].extend(
            percentageMatrix[index2_in_percentage_matrix][0])

        percentageMatrix[index1_in_percentage_matrix][1] = percentageMatrix[
            index2_in_percentage_matrix][1]

        del percentageMatrix[index2_in_percentage_matrix]

    elif (index2_in_percentage_matrix) == (index1_in_percentage_matrix + 2):
        percentageMatrix[index1_in_percentage_matrix + 1][0].extend(
            percentageMatrix[index2_in_percentage_matrix][0])

        percentageMatrix[index1_in_percentage_matrix][0].extend(
            percentageMatrix[index1_in_percentage_matrix + 1][0])

        percentageMatrix[index1_in_percentage_matrix][1] = percentageMatrix[
            index2_in_percentage_matrix][1]

        del percentageMatrix[index2_in_percentage_matrix]
        del percentageMatrix[index1_in_percentage_matrix + 1]

    return percentageMatrix

In [164]:
dataFrame = processData.processingData()
#address is: /home/netlab/Desktop/thesis/data/1node1-3-5/
#/home/netlab/Desktop/thesis/data/500f80271400/
data = dataFrame.copy() #copying the dataFrame to have a copy of not edited data

data = processData.dataFrameManipulation(data)

the address of the collected data files (not alligned files or CSV files): /home/sepehr/thesis/data/500f80271400/
['500f80271400.txt']
here
500f80271400.txt is in csvChecker

we have the csv file: pulling out data

   col1                time  CU
0     0 2018-11-13 02:01:32  45
1     1 2018-11-13 02:01:38  45
2     2 2018-11-13 02:01:44  51
3     3 2018-11-13 02:01:50  53
4     4 2018-11-13 02:01:56  45
now we have the processed data from pandas
please enter how long would be the chunk minutes? 5
removing weekends from the data


In [170]:
cuTrans_5min = processData.markovianTransitionMatrixDegree1(data, numberOfStates, "CU")
normalizedCuTrans_5min = processData.normalizingTransMatrix(cuTrans_5min)


In [173]:
reload(oldLumping)
for i in range(1):
    percentageMatrix_list, irreducible_matrix = preparingMatrixForLumping(normalizedCuTrans_5min[29])
    result = oldLumping.lumping(irreducible_matrix, percentageMatrix_list, False)

0.99999994
0.99999994
we have these many sectors to check:  607


In [179]:
result[20]

(1.0,
 25.528564453125,
 array([[0.40645161, 0.10638298, 0.        , 0.        , 0.        ,
         0.        ],
        [0.        , 0.72575251, 0.        , 0.        , 0.        ,
         0.        ],
        [0.        , 0.        , 0.        , 0.        , 0.        ,
         0.        ],
        [0.        , 0.66666667, 0.        , 0.        , 0.        ,
         0.        ],
        [1.        , 0.        , 0.        , 0.        , 0.        ,
         0.        ],
        [0.        , 1.        , 0.        , 0.        , 0.        ,
         0.        ]]),
 [-1, 5, 26, 42, 46, 47, 48])

In [6]:
data = pd.read_pickle("main_dataFrame")

In [11]:
def dayCalculator(x):
    years = x["time"].year - data["time"][0].year
    months = x["time"].month - data["time"][0].month
    days = x["time"].day - data["time"][0].day
    return ((years*12*30) + (months*30) + days)
data["day"] = data.apply(lambda x: dayCalculator(x), axis = 1)

KeyboardInterrupt: 

In [166]:
uniqueDays = []
uniqueDays.extend(data.apply(lambda x: x["day"] if x["day"] not in uniqueDays else np.inf, axis = 1))
uniqueDays = list(set(uniqueDays))

In [167]:
data_within_30Days = data.loc[data["day"].isin(days30)].copy()
numberOfStates = 255
cuTrans_30Days = processData.markovianTransitionMatrixDegree1(data_within_30Days, numberOfStates, "CU")
normalizedCuTrans_30Days = processData.normalizingTransMatrix(cuTrans_30Days)

steadyState_30days = np.zeros(shape=(normalizedCuTrans_30Days.shape[0],
                                     normalizedCuTrans_30Days.shape[1]))

for i in range(normalizedCuTrans_30Days.shape[0]):
    steadyState_30days[i] = abs(pysal.spatial_dynamics.ergodic.steady_state(normalizedCuTrans_30Days[i]))

In [168]:
for x in range(48):
    data["corr" + str(x + 1)] = np.inf

data.head()

col1                time  CU    CU/255  timeIndex  weekDay  day  corr1  \
0     0 2018-11-12 19:01:32  45  0.176471        228        0    0    inf   
1     1 2018-11-12 19:01:38  45  0.176471        228        0    0    inf   
2     2 2018-11-12 19:01:44  51  0.200000        228        0    0    inf   
3     3 2018-11-12 19:01:50  53  0.207843        228        0    0    inf   
4     4 2018-11-12 19:01:56  45  0.176471        228        0    0    inf   

   corr2  corr3  ...  corr39  corr40  corr41  corr42  corr43  corr44  corr45  \
0    inf    inf  ...     inf     inf     inf     inf     inf     inf     inf   
1    inf    inf  ...     inf     inf     inf     inf     inf     inf     inf   
2    inf    inf  ...     inf     inf     inf     inf     inf     inf     inf   
3    inf    inf  ...     inf     inf     inf     inf     inf     inf     inf   
4    inf    inf  ...     inf     inf     inf     inf     inf     inf     inf   

   corr46  corr47  corr48  
0     inf     inf     inf  
1     inf     inf     inf  
2     inf     inf     inf  
3     inf     inf     inf  
4     inf     inf     inf  

[5 rows x 55 columns]

In [7]:
for j in uniqueDays:
    print(j)
    for i in range(48):
        data_correlation = data.loc[(data["timeIndex"] == i) & (data["day"] == j)].copy()
        if len(data_correlation) == 0:
            continue
        cuTran_corr = processData.markovianTransitionMatrixDegree1(data_correlation, numberOfStates, "CU")
        for x in range(cuTran_corr[-1].shape[0]):
            if np.sum(cuTran_corr[-1][x]) == 0:
                continue
            cuTran_corr[-1][x] = cuTran_corr[-1][x] / np.sum(cuTran_corr[-1][x])
        steadyState_corr = abs(pysal.spatial_dynamics.ergodic.steady_state(cuTran_corr[-1]))

        steadyState_corr_normalize = (steadyState_corr - np.mean(steadyState_corr)) / (
            np.std(steadyState_corr) * len(steadyState_corr))
        
        correlationDistance = []
        
        for x in range(48):
            ss_normalize = (steadyState_30days[x] - np.mean(steadyState_30days[x])) / (
                np.std(steadyState_30days[x]))
            data["corr" + str(x + 1)].loc[(data["timeIndex"] == i) & (data["day"] == j)] = signal.correlate(
                steadyState_corr_normalize, ss_normalize, mode="valid")[0]

NameError: name 'uniqueDays' is not defined

In [104]:
name = "/home/sepehr/thesis/APDataML/normalBoundaries_30min.pickle"
with open(name, 'rb') as handle:
    normalLumps = pickle.load(handle)

for i in range(len(normalLumps)):
    if len(normalLumps[i]) == 0:
        continue

    for j in range(len(normalLumps[i])):
        for x in range(len(normalLumps[i][j][3])):
            normalLumps[i][j][3][x] += 1

percentageArray = []
for i in range(48):
    name = "/home/sepehr/thesis/APDataML/pickles/normal_lumping_percentage_" + str(i) + ".pickle"
    with open(name, 'rb') as handle:
        percentageArray.append(pickle.load(handle))



In [188]:
boundaries

array([ 24.31372549,  46.2745098 ,  58.03921569,  77.25490196,
        69.01960784, 100.        ])

In [209]:
data["CU"][11829]

56

In [217]:
data_cpy = data.copy()
data_cpy["currentCU"] = np.inf
data_cpy["prevCU"] = np.inf
data_cpy["prev2CU"] = np.inf
data_cpy = data_cpy.apply(lambda x: classifying(data_cpy, x, boundaries), axis = 1)
# iterPandas = data_cpy.loc[(data["timeIndex"] == 32)].copy()


In [214]:
def classifying(data, x, boundaries):
    occupiedBandwidth = (x["CU"] / 255) * 100
    for i in range(len(boundaries)):
        if occupiedBandwidth <= boundaries[i]:
            x["currentCU"] = i

            
    if (x['col1'] - 1) > 0 and (x['col1'] - 1) in data["col1"]:
        for i in range(len(boundaries)):
            if (data["CU/255"][x['col1'] - 1] *100) <= boundaries[i]:
                x["prevCU"] = i
    else:
        x["prevCU"] = 0
                
    if (x['col1'] - 2) > 0 and (x['col1'] - 2) in data["col1"]:
        for i in range(len(boundaries)):
            if (data["CU/255"][x['col1'] - 2] *100) <= boundaries[i]:
                x["prev2CU"] = i
    else:
        x["prev2CU"] = 0
    

In [220]:
data.head()

col1                time  CU    CU/255  timeIndex  weekDay  day     corr1  \
0     0 2018-11-12 19:01:32  45  0.176471         38        0    0  0.499839   
1     1 2018-11-12 19:01:38  45  0.176471         38        0    0  0.499839   
2     2 2018-11-12 19:01:44  51  0.200000         38        0    0  0.499839   
3     3 2018-11-12 19:01:50  53  0.207843         38        0    0  0.499839   
4     4 2018-11-12 19:01:56  45  0.176471         38        0    0  0.499839   

      corr2     corr3     corr4     corr5  month  
0  0.529556  0.744314  0.633685  0.509328     11  
1  0.529556  0.744314  0.633685  0.509328     11  
2  0.529556  0.744314  0.633685  0.509328     11  
3  0.529556  0.744314  0.633685  0.509328     11  
4  0.529556  0.744314  0.633685  0.509328     11

In [263]:
for timeIndexes in range(25, 26):
    timeIndexes = 32
    print(timeIndexes)
    boundaries = np.array([])
    if len(normalLumps[timeIndexes]) == 0:
        continue

    # print(normalLumps[timeIndexes][0][3])
    # normalLumps[timeIndexes]
    
    for increament in range(-5, +6, +1):
        maintainedMat = normalLumps.copy()
        maintainedMat[timeIndexes][0][3][np.abs(increament) + 1] += np.sign(increament)
        for i in range(1, len(normalLumps[timeIndexes][0][3]) - 1):
            bound = maintainedMat[timeIndexes][0][3][i]
            counter = 0
            for j in range(len(percentageArray[timeIndexes])):
                if percentageArray[timeIndexes][j][2] == False:
                    counter += 1
                if counter == bound:
                    boundaries = np.append(boundaries, percentageArray[timeIndexes][j][1])
                    break
        boundaries = np.append(boundaries,100)
        print(boundaries)

        x = normalLumps[timeIndexes]
        for i in range(x[0][2].shape[0]):
            x[0][2][i] = x[0][2][i]/np.sum(x[0][2][i])
        weight = abs(pysal.spatial_dynamics.ergodic.steady_state(x[0][2]))

        XArraysForLearning, YArraysForLearning, XArraysForTesting, YArraysForTesting, boundaries = simpleLogisticRegression(
            data, normalLumps[timeIndexes][0][2], timeIndexes, 30, boundaries)
        print("starting tensor")
        tensorFlowLossFunction(XArraysForLearning, YArraysForLearning, XArraysForTesting, YArraysForTesting, boundaries)

32
[ 24.31372549  46.2745098   58.03921569  77.25490196  69.01960784
 100.        ]
start training set generation
[1.         0.         0.         0.         0.         0.
 1.         0.         0.         0.         0.         0.
 1.         0.         0.         0.         0.         0.
 1.         0.         0.         0.         0.         0.
 1.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         1.
 0.23780582 0.26178153 0.70168161 0.86559653 0.40310791 0.95606365
 0.04393635 0.         0.         0.         0.         0.11778304]
[1.         0.         0.         0.         0.         0.
 1.         0.         0.         0.         0.         0.
 1.         0.         0.         0.         0.         0.
 1.         0.         0.         0.         0.         0.
 0.         1.         0.         0.         0.         0.
 0.         0.         0.         0.       

[ 0.          1.          0.          0.          0.          0.
  0.          1.          0.          0.          0.          0.
  0.          1.          0.          0.          0.          0.
  1.          0.          0.          0.          0.          0.
  1.          0.          0.          0.          0.          0.
  0.          0.          0.          0.          0.          0.
  0.          0.          0.          0.          0.          1.
  0.23780582  0.26178153  0.70168161  0.86559653  0.40310791  0.95606365
  0.04393635  0.          0.          0.          0.         -0.29924289]
[ 0.          1.          0.          0.          0.          0.
  0.          1.          0.          0.          0.          0.
  1.          0.          0.          0.          0.          0.
  1.          0.          0.          0.          0.          0.
  1.          0.          0.          0.          0.          0.
  0.          0.          0.          0.          0.          0.
  0.    

 0.04393635 0.         0.         0.         0.         0.03226086]
[ 1.          0.          0.          0.          0.          0.
  0.          1.          0.          0.          0.          0.
  0.          1.          0.          0.          0.          0.
  1.          0.          0.          0.          0.          0.
  0.          1.          0.          0.          0.          0.
  0.          0.          0.          0.          0.          0.
  0.          0.          0.          0.          0.          1.
  0.37318403  0.40264354  0.82532313  0.8984276   0.50361893  0.18601853
  0.79252326  0.02145821  0.          0.          0.         -0.11778304]
[0.         1.         0.         0.         0.         0.
 0.         1.         0.         0.         0.         0.
 1.         0.         0.         0.         0.         0.
 0.         1.         0.         0.         0.         0.
 1.         0.         0.         0.         0.         0.
 0.         0.         0.         0

 0.04393635 0.         0.         0.         0.         0.0901511 ]
[ 1.          0.          0.          0.          0.          0.
  1.          0.          0.          0.          0.          0.
  1.          0.          0.          0.          0.          0.
  1.          0.          0.          0.          0.          0.
  1.          0.          0.          0.          0.          0.
  0.          0.          0.          0.          0.          0.
  0.          0.          0.          0.          0.          1.
  0.26739499  0.28971773  0.71083526  0.83509622  0.41735529  0.95606365
  0.04393635  0.          0.          0.          0.         -0.03509132]
[1.         0.         0.         0.         0.         0.
 1.         0.         0.         0.         0.         0.
 1.         0.         0.         0.         0.         0.
 1.         0.         0.         0.         0.         0.
 1.         0.         0.         0.         0.         0.
 0.         0.         0.         0

  0.79252326  0.02145821  0.          0.          0.         -0.17979311]
[0.         1.         0.         0.         0.         0.
 0.         1.         0.         0.         0.         0.
 0.         1.         0.         0.         0.         0.
 0.         1.         0.         0.         0.         0.
 0.         1.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         1.
 0.06098446 0.08356349 0.395519   0.59528142 0.20139607 0.18601853
 0.79252326 0.02145821 0.         0.         0.         0.1008047 ]
[0.         1.         0.         0.         0.         0.
 0.         1.         0.         0.         0.         0.
 0.         1.         0.         0.         0.         0.
 0.         1.         0.         0.         0.         0.
 0.         1.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0

...

[0.         1.         0.         0.         0.         0.
 0.         1.         0.         0.         0.         0.
 0.         1.         0.         0.         0.         0.
 1.         0.         0.         0.         0.         0.
 1.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         1.
 0.04876373 0.07288863 0.37742321 0.58706676 0.19190991 0.95606365
 0.04393635 0.         0.         0.         0.         0.16430305]
[ 0.          1.          0.          0.          0.          0.
  0.          1.          0.          0.          0.          0.
  1.          0.          0.          0.          0.          0.
  1.          0.          0.          0.          0.          0.
  0.          1.          0.          0.          0.          0.
  0.          0.          0.          0.          0.          0.
  0.          0.          0.          0.          0.          

  0.62153475  0.1434311   0.          0.          0.         -0.83076856]
[0.         1.         0.         0.         0.         0.
 0.         1.         0.         0.         0.         0.
 0.         1.         0.         0.         0.         0.
 0.         0.         1.         0.         0.         0.
 1.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         1.
 0.08427497 0.10287308 0.47084199 0.69726107 0.24555912 0.95606365
 0.04393635 0.         0.         0.         0.         0.21985948]
[ 0.          1.          0.          0.          0.          0.
  0.          1.          0.          0.          0.          0.
  0.          0.          1.          0.          0.          0.
  1.          0.          0.          0.          0.          0.
  0.          1.          0.          0.          0.          0.
  0.          0.          0.          0.          0. 

[ 0.          1.          0.          0.          0.          0.
  1.          0.          0.          0.          0.          0.
  0.          1.          0.          0.          0.          0.
  0.          1.          0.          0.          0.          0.
  0.          1.          0.          0.          0.          0.
  0.          0.          0.          0.          0.          0.
  0.          0.          0.          0.          0.          0.
  0.11918594  0.13718947  0.51972736  0.71054157  0.28885453  0.18601853
  0.79252326  0.02145821  0.          0.          0.         -0.11954515]
[1.         0.         0.         0.         0.         0.
 0.         1.         0.         0.         0.         0.
 0.         1.         0.         0.         0.         0.
 0.         1.         0.         0.         0.         0.
 0.         1.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.         0.        

 0.04393635 0.         0.         0.         0.         0.28768207]
[1.         0.         0.         0.         0.         0.
 0.         1.         0.         0.         0.         0.
 0.         1.         0.         0.         0.         0.
 1.         0.         0.         0.         0.         0.
 0.         1.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.09222861 0.11014894 0.43688365 0.64169596 0.23144733 0.18601853
 0.79252326 0.02145821 0.         0.         0.         0.07095174]
[ 0.          1.          0.          0.          0.          0.
  0.          1.          0.          0.          0.          0.
  1.          0.          0.          0.          0.          0.
  0.          1.          0.          0.          0.          0.
  0.          1.          0.          0.          0.          0.
  0.          0.          0.          0.          0.       

KeyboardInterrupt: 

In [155]:
for i in range(len(arrs)):
    print(i,arrs[i][5])

0 [-1, 16, 27, 45, 70, 82, 85]
1 [-1, 16, 27, 46, 70, 82, 85]
2 [-1, 16, 27, 47, 70, 82, 85]
3 [-1, 16, 27, 47, 71, 82, 85]
4 [-1, 16, 27, 48, 70, 82, 85]
5 [-1, 16, 27, 48, 71, 82, 85]
6 [-1, 16, 27, 49, 70, 82, 85]
7 [-1, 16, 27, 49, 71, 82, 85]
8 [-1, 16, 27, 50, 70, 82, 85]
9 [-1, 16, 27, 50, 71, 82, 85]
10 [-1, 16, 27, 51, 70, 82, 85]
11 [-1, 16, 27, 51, 71, 82, 85]
12 [-1, 16, 27, 52, 70, 82, 85]
13 [-1, 16, 27, 52, 71, 82, 85]
14 [-1, 16, 28, 45, 70, 82, 85]
15 [-1, 16, 28, 46, 70, 82, 85]
16 [-1, 16, 28, 47, 70, 82, 85]
17 [-1, 16, 28, 47, 71, 82, 85]
18 [-1, 16, 28, 48, 70, 82, 85]
19 [-1, 16, 28, 48, 71, 82, 85]
20 [-1, 16, 28, 49, 70, 82, 85]
21 [-1, 16, 28, 49, 71, 82, 85]
22 [-1, 16, 28, 50, 70, 82, 85]
23 [-1, 16, 28, 50, 71, 82, 85]
24 [-1, 16, 28, 51, 70, 82, 85]
25 [-1, 16, 28, 51, 71, 82, 85]
26 [-1, 16, 28, 52, 70, 82, 85]
27 [-1, 16, 28, 52, 71, 82, 85]
28 [-1, 16, 29, 45, 70, 82, 85]
29 [-1, 16, 29, 46, 70, 82, 85]
30 [-1, 16, 29, 47, 70, 82, 85]
31 [-1, 16, 29, 47

In [171]:
print(arrs[729][5], arrs[392][5])

[-1, 18, 43, 55, 72, 82, 85] [-1, 18, 29, 45, 70, 82, 85]


In [299]:
def simpleLogisticRegression(data, transMat, timeIndexes, minuteSplit, boundaries):
    from sklearn.utils import shuffle
    warnings.filterwarnings('always')
    reg = "l2"
    solvers = "lbfgs"
    clf = LogisticRegression(penalty = reg, max_iter = 100000, random_state = 0,
                             solver = solvers , multi_class = 'multinomial')
    accuracyValue = 0
    numOfElements = 0
    f1scoreValue = 0
    precisionValue = 0
    recallValue = 0
    prevRowTrain = np.inf
    prevCU = np.inf

    sampleIntervals = 6 #seconds
    minuteSplit = 30 #minutes
    numOfSamples = minuteSplit * 60 / sampleIntervals
    # numberOfDays = len(numOfDays)
    days = np.zeros(7)
    numOfThirtyMinsPerDay = np.zeros(int((24 * 60) / minuteSplit)) #in this case 48
#     which6SecondsPerPeriod = np.zeros(int(minuteSplit * 60 / sampleIntervals)) #in this case 300
    prevRowTrain = np.inf
    prevCU = np.inf

    XArraysForLearning = []
    YArraysForLearning = []
    XArraysForTesting = []
    YArraysForTesting = []

    x = timeIndexes
    wholeDataFrame = data.loc[(data["timeIndex"] == x)].copy()
    
    wholeDataFrame["cuClass"] = wholeDataFrame["CU"].apply(lambda x: classifying(x, boundaries))
    
#     iterPandas = iterPandas.sample(frac = 1)

#     wholeDataFrame = iterPandas.iloc[:int(np.floor(0.8 * len(iterPandas)))].copy()

    

    stackCounter = 0
    prevCU = 0
    prev2CU = 0
    prev3CU = 0
    prev4CU = 0
    prev5CU = 0
    print("start training set generation")
    numberOfFeatures = (5*len(boundaries)) + 12 + 5 + len(boundaries) + 1 #month and correlations and logDiff
    XArraysForLearning = np.zeros(shape=(len(wholeDataFrame), numberOfFeatures))
    YArraysForLearning = np.zeros(shape=(len(wholeDataFrame), len(boundaries)))
#     print(len(trainingDataFrame))
    counter = 0
    pandasIndexCounter = 0
    for index, row in wholeDataFrame.iterrows():
        month = int(row["month"])
        XArraysForLearning[pandasIndexCounter, prev5CU] = 1
        XArraysForLearning[pandasIndexCounter, len(boundaries) + prev4CU] = 1
        XArraysForLearning[pandasIndexCounter, 2 * len(boundaries) + prev3CU] = 1
        XArraysForLearning[pandasIndexCounter, 3 * len(boundaries) + prev2CU] = 1
        XArraysForLearning[pandasIndexCounter, 4 * len(boundaries) + prevCU] = 1
        XArraysForLearning[pandasIndexCounter, 5 * len(boundaries) + month] = 1
        for corrs in range(5):
            XArraysForLearning[pandasIndexCounter, 5 * len(boundaries) + 12 + corrs] = row["corr" + str(corrs + 1)]
        for i in range(len(transMat[prevCU])):
            XArraysForLearning[pandasIndexCounter, 5 * len(boundaries) + 12 + 5 + i] = transMat[prevCU, i]
        XArraysForLearning[pandasIndexCounter, 5 * len(boundaries) + 12 + 5 + len(boundaries)] = row["normalLogDiff"]
        YArraysForLearning[pandasIndexCounter, row["cuClass"]] = 1
#         print(XArraysForLearning[pandasIndexCounter])

        which6SecondsPerPeriod = 0
        prev5CU = prev4CU
        prev4CU = prev3CU
        prev3CU = prev2CU
        prev2CU = prevCU
        prevCU = row["cuClass"]
        pandasIndexCounter += 1

    XArraysForLearning, YArraysForLearning = shuffle(XArraysForLearning, YArraysForLearning, random_state=0)
    XArraysForTraining = XArraysForLearning[:int(0.8*len(XArraysForLearning))]
    YArraysForTraining = YArraysForLearning[:int(0.8*len(YArraysForLearning))]
    XArraysForTesting = XArraysForLearning[int(0.8*len(XArraysForLearning)):]
    YArraysForTesting = YArraysForLearning[int(0.8*len(YArraysForLearning)):]
    print(XArraysForTraining.shape[0])
    print(XArraysForTesting.shape[0])


    return XArraysForTraining, YArraysForTraining, XArraysForTesting, YArraysForTesting, boundaries


In [239]:
data["log"] = np.log(data["CU"])
data["logDiff"] = data["log"].diff()

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:1: RuntimeWarning:

divide by zero encountered in log

/home/sepehr/.local/lib/python3.6/site-packages/pandas/core/algorithms.py:1819: RuntimeWarning:

invalid value encountered in subtract



In [298]:
# x = data.loc[data["logDiff"] != -np.inf]
# x = x.loc[x["log"] != -np.inf]
# x = x.loc[x["log"] != np.nan]
# x= x.drop([0])
# x["logDiff"] = (x["logDiff"] - np.min(x["logDiff"]))
# np.min(x["normalLog"])
# x["normalLog"] = (x["log"] / np.max(x["log"]))
x["normalLogDiff"] = x["logDiff"] / np.max(x["logDiff"]) 

In [305]:
# for increament in range(-5, +6, +1):
boundaries = np.array([])
maintainedMat = normalLumps.copy()
maintainedMat[timeIndexes][0][3][np.abs(increament) + 1] += np.sign(increament)
timIndexes = 32
for i in range(1, len(arrs[195][5]) - 1):
    bound = arrs[195][5][i] + 1
#     if i == 2:
#         bound += 1
    counter = 0
    for j in range(len(percentageArray[timeIndexes])):
        if percentageArray[timeIndexes][j][2] == False:
            counter += 1
        if counter == bound:
            boundaries = np.append(boundaries, percentageArray[timeIndexes][j][1])
            break
boundaries = np.append(boundaries,100)
print(boundaries)

# x = normalLumps[timeIndexes]
# for i in range(x[0][2].shape[0]):
#     x[0][2][i] = x[0][2][i]/np.sum(x[0][2][i])
# weight = abs(pysal.spatial_dynamics.ergodic.steady_state(x[0][2]))

XArraysForLearning, YArraysForLearning, XArraysForTesting, YArraysForTesting, boundaries = simpleLogisticRegression(
    x, arrs[195][2], timeIndexes, 30, boundaries)
print("starting tenor")
tensorFlowLossFunction(XArraysForLearning, YArraysForLearning, XArraysForTesting, YArraysForTesting, boundaries)

[ 22.35294118  47.05882353  61.17647059  78.03921569  88.23529412
 100.        ]
start training set generation
19095
4774
starting tenor
Initialized
for epoch and loss: 0 210.12441486640262
0.1936346476510067
for epoch and loss: 1 80.33753948083658
0.5233326342281879
for epoch and loss: 2 50.632446218657016
0.7282403523489933
for epoch and loss: 3 44.25568899372283
0.7558724832214765
for epoch and loss: 4 41.142326943826376
0.7716547818791947
for epoch and loss: 5 39.10030232499908
0.7842911073825504
for epoch and loss: 6 37.67551852232658
0.7906354865771812
for epoch and loss: 7 36.71273653939263
0.792890100671141
for epoch and loss: 8 36.03444469375097
0.7947776845637584
for epoch and loss: 9 35.57059177936321
0.7980285234899329
for epoch and loss: 10 35.16042786156568
0.8004928691275168
for epoch and loss: 11 34.840984357283446
0.8013842281879194
for epoch and loss: 12 34.528702575888424
0.8023280201342282
for epoch and loss: 13 34.282814851543236
0.8030096476510067
for epoch and lo

for epoch and loss: 133 26.17293210637649
0.8427537751677853
for epoch and loss: 134 26.139816037760482
0.8439072986577181
for epoch and loss: 135 26.1090783688846
0.8434354026845637
for epoch and loss: 136 26.07563498196186
0.8439072986577181
for epoch and loss: 137 26.049208881070946
0.8443267617449665
for epoch and loss: 138 26.037419120737372
0.8440121644295302
for epoch and loss: 139 26.007479168424673
0.8433305369127517
for epoch and loss: 140 25.975041923906986
0.8442218959731543
for epoch and loss: 141 25.95122359743054
0.8451656879194631
for epoch and loss: 142 25.93020397544707
0.8442743288590604
for epoch and loss: 143 25.88067389174596
0.8450083892617449
for epoch and loss: 144 25.858950061286052
0.8461619127516778
for epoch and loss: 145 25.85230961101967
0.8444840604026845
for epoch and loss: 146 25.821114124067677
0.8455327181208053
for epoch and loss: 147 25.778187956585978
0.8447986577181208
for epoch and loss: 148 25.753793249194253
0.8458997483221476
for epoch and lo

for epoch and loss: 267 23.62113249541928
0.8571728187919463
for epoch and loss: 268 23.61180788078564
0.8574874161073825
for epoch and loss: 269 23.58444340917087
0.8585360738255033
for epoch and loss: 270 23.56352903698915
0.8581166107382551
for epoch and loss: 271 23.563198620841003
0.8576971476510067
for epoch and loss: 272 23.533706591433333
0.858169043624161
for epoch and loss: 273 23.52977638756668
0.8575398489932886
for epoch and loss: 274 23.517216349608148
0.8576971476510067
for epoch and loss: 275 23.513849239221354
0.8574874161073825
for epoch and loss: 276 23.490168622676148
0.858064177852349
for epoch and loss: 277 23.492743412120227
0.8582739093959731
for epoch and loss: 278 23.465827049024956
0.8577495805369127
for epoch and loss: 279 23.44824770152968
0.8586933724832215
for epoch and loss: 280 23.44538525766973
0.8579593120805369
for epoch and loss: 281 23.431989173761153
0.8588506711409396
for epoch and loss: 282 23.414243966941065
0.8593225671140939
for epoch and los

for epoch and loss: 401 22.29743163217634
0.8627307046979866
for epoch and loss: 402 22.276881669191713
0.8626258389261745
for epoch and loss: 403 22.255934555258523
0.8629928691275168
for epoch and loss: 404 22.26926411878342
0.8623112416107382
for epoch and loss: 405 22.250029179873884
0.8624685402684564
for epoch and loss: 406 22.25439993967146
0.8626782718120806
for epoch and loss: 407 22.25590188071232
0.8621015100671141
for epoch and loss: 408 22.22631451267525
0.8635696308724832
for epoch and loss: 409 22.231227308311738
0.8630977348993288
for epoch and loss: 410 22.21923271601632
0.8630453020134228
for epoch and loss: 411 22.200873221326997
0.8629404362416108
for epoch and loss: 412 22.201449695049515
0.863307466442953
for epoch and loss: 413 22.20291556927981
0.8634647651006712
for epoch and loss: 414 22.195404190345098
0.8625734060402684
for epoch and loss: 415 22.190227441339673
0.8637269295302014
for epoch and loss: 416 22.18269486395304
0.8630453020134228
for epoch and los

for epoch and loss: 535 21.459924432255278
0.8666107382550335
for epoch and loss: 536 21.458969023403704
0.8655620805369127
for epoch and loss: 537 21.472218881517442
0.8651426174496645
for epoch and loss: 538 21.44281202674713
0.8655620805369127
for epoch and loss: 539 21.461409520782887
0.8656669463087249
for epoch and loss: 540 21.445832214099458
0.8656145134228188
for epoch and loss: 541 21.447416971193867
0.865981543624161
for epoch and loss: 542 21.432340660351244
0.865876677852349
for epoch and loss: 543 21.428127023197668
0.8661912751677853
for epoch and loss: 544 21.430874808522674
0.8664534395973155
for epoch and loss: 545 21.439263574228974
0.8656145134228188
for epoch and loss: 546 21.426240697003056
0.865876677852349
for epoch and loss: 547 21.42300152938638
0.8661388422818792
for epoch and loss: 548 21.405693537436886
0.8656669463087249
for epoch and loss: 549 21.409487839513172
0.8655620805369127
for epoch and loss: 550 21.393177749326558
0.8662437080536913
for epoch and

for epoch and loss: 669 20.92816933369477
0.8677642617449665
for epoch and loss: 670 20.944422811469764
0.8673447986577181
for epoch and loss: 671 20.931222169991308
0.8681312919463087
for epoch and loss: 672 20.92388393414901
0.8672399328859061
for epoch and loss: 673 20.91151154921358
0.8671875
for epoch and loss: 674 20.91519584271732
0.8673447986577181
for epoch and loss: 675 20.927874769940473
0.8672923657718121
for epoch and loss: 676 20.900411413820006
0.8680264261744967
for epoch and loss: 677 20.919638860945742
0.868393456375839
for epoch and loss: 678 20.916143865393302
0.8674496644295302
for epoch and loss: 679 20.90127581717983
0.8680788590604027
for epoch and loss: 680 20.890410173659337
0.8675020973154363
for epoch and loss: 681 20.89941759877556
0.8676069630872483
for epoch and loss: 682 20.893912328169662
0.8681837248322147
for epoch and loss: 683 20.88640120845513
0.8668729026845637
for epoch and loss: 684 20.88666705957195
0.8679215604026845
for epoch and loss: 685 20

In [304]:
def tensorFlowLossFunction(XArraysForLearning, YArraysForLearning, XArraysForTesting, YArraysForTesting, boundaries):
    batch_size = 64
    learning_rate = 0.001
    beta = 0.1
    numOfEpochs = 800
    graph = tf.Graph()
    with graph.as_default():
        x = tf.placeholder(tf.float32, shape = (batch_size, XArraysForLearning.shape[1]))
        y_ = tf.placeholder(tf.float32, shape = (batch_size, YArraysForLearning.shape[1]))
#         print(weights.dtype)
#         print(weights.shape)
#         print(XArraysForLearning.shape[1], YArraysForLearning.shape[1])
#         multiDistrib = np.vstack((mult, mult))
#         for i in range(batch_size - 2):
#             multiDistrib = np.vstack((multiDistrib, mult))
        W = tf.Variable(tf.truncated_normal([XArraysForLearning.shape[1], YArraysForLearning.shape[1]]), name="weights", dtype=tf.float32)
        b = tf.Variable(tf.truncated_normal([YArraysForLearning.shape[1]]), dtype=tf.float32)

        tf_test_dataset64 = tf.constant(XArraysForTesting)
        tf_test_dataset = tf.cast(tf_test_dataset64, tf.float32)


        beta = 0.05
        logits = tf.matmul(x, W)
        train_prediction = tf.nn.softmax(logits)
        # train_prediction = tf.nn.softmax_cross_entropy_with_logits_v2(labels = y_, logits = logits)
        test_prediction = tf.nn.softmax(tf.add(tf.matmul(tf_test_dataset, W),b))

        # x = XArraysForLearning[0:(0 + batch_size), :]
        # y_ = tf.Variable(YArraysForLearning[0:(0 + batch_size), :])

        # loss = assymetricLossFunction(train_prediction, y_, boundaries)
        # loss = assymetricLossFunction(train_prediction, y_, boundaries)
        
        loss = tf.nn.softmax_cross_entropy_with_logits_v2(logits = logits, labels = y_)
#         dist = tfp.distributions.Multinomial(total_count=1, logits=logits)
#         loss = loss - (dist.log_prob(mult))
        # regularizer = tf.nn.l2_loss(W)
        # loss = tf.reduce_mean(loss + beta * regularizer)
        # loss = tf.nn.softmax_cross_entropy_with_logits_v2(logits = train_prediction, labels = y_)
        optimizer = tf.train.AdamOptimizer().minimize(loss)

        prevAcc = 0

    with tf.Session(graph=graph) as session:
        tf.global_variables_initializer().run()
        print("Initialized")

        numberOfBatchIteration = int(XArraysForLearning.shape[0] / batch_size)
        restOfData = XArraysForLearning.shape[0] % batch_size
        if restOfData != 0:
            numberOfBatchIteration += 1

        accuracy_earlyStop = 0
        earlyStoppingCounter = 0
        
        prevW = W
        for epoch in range(numOfEpochs):
            accuracyValue = 0
            lossValue = 0
            totalBatch = 0
            i = 0
            randomize = np.arange(XArraysForLearning.shape[0])
            np.random.shuffle(randomize)
            XArraysForLearning = XArraysForLearning[randomize]
            YArraysForLearning = YArraysForLearning[randomize]

            for iteration in range(numberOfBatchIteration):
                if (iteration == numberOfBatchIteration - 1) and restOfData != 0:
                    break
                    batch_data = XArraysForLearning[i:, :]
                    batch_labels = YArraysForLearning[i:, :]

                else:
                    batch_data = XArraysForLearning[i:(i + batch_size), :]
                    batch_labels = YArraysForLearning[i:(i + batch_size), :]

                    i += batch_size


                feed_dict = {x : batch_data, y_ : batch_labels}
                _, predictions, l = session.run([optimizer, train_prediction, loss], feed_dict=feed_dict)

#                 print(l)
                lossValue *= (iteration)
                lossValue += (np.sum(l))
                lossValue /= (iteration + 1)
                totalBatch += batch_size
                # print(accuracy(batch_data, batch_labels))
                accuracyValue += accuracy(predictions, batch_labels) * batch_size
                if accuracy(test_prediction.eval(), YArraysForTesting) < prevAcc and earlyStoppingCounter == 100:
                    print(prevAcc)
                    break
                
                elif accuracy(test_prediction.eval(), YArraysForTesting) < prevAcc:
                    earlyStoppingCounter += 1
                
                elif accuracy(test_prediction.eval(), YArraysForTesting) >= prevAcc:
                    earlyStoppingCounter = 0

#             print("Minibatch step {0}".format(step))
            # print("training Acc is: {:.3f}".format(accuracy(predictions,batch_labels)))
#             prevAcc = accuracy(test_prediction.eval(), YArraysForTesting)
            print("for epoch and loss:", epoch, lossValue)
            totalAccuracy = accuracyValue/totalBatch
            print(accuracyValue/totalBatch)
            if accuracy(test_prediction.eval(), YArraysForTesting) > accuracy_earlyStop:
                accuracy_earlyStop = accuracy(test_prediction.eval(), YArraysForTesting)

            else:
                earlyStoppingCounter += 1

            if earlyStoppingCounter == 50:
                break



        # print(session.run(W))
        predictionResult = test_prediction.eval()
        accResult = testAccuracy(predictionResult , YArraysForTesting)
        print("Penalty Value: {:.3f}".format(assymetricPredictionScore(predictionResult, YArraysForTesting, boundaries)))
#         print(W.eval())
        if accuracy_earlyStop > accResult:
            print("accuracy Result is: ", accuracy_earlyStop)
        else:
            print("accuracy Result is: ", accResult)
            
def lossFunctionWithMult(mult, logits, y_):
    sess = tf.Session()
    arr = tf.Variable(tf.zeros(mult.shape, tf.int32))

    tf.initialize_all_variables().run(session=sess)
    
    pred = tf.argmax(logits, 1)
#     print(pred)
#     print(arr)
#     print(mult.shape[0])
#     print(sess.run(pred))
    for i in range(mult.shape[0]):
        tf.scatter_update(arr, [i, pred[i]], 1)
    print(sess.run(arr))
        
    xi =  tf.nn.softmax_cross_entropy_with_logits_v2(logits = logits, labels = y_)
    xi = xi - tf.log(multinomial.pmf(arr, 1, mult))
    
    
#     correctLableIndex = np.argmax(trueLables, 1)
#     predictionIndex = np.argmax(predictedLables, 1)

#     diffPercentage = np.zeros(shape = (predictedLables.shape))

#     penalties = np.zeros(shape = (predictedLables.shape))

#     for index in range(predictedLables.shape[0]):
#         diffPercentage[index] = boundaries[correctLableIndex[index]] - boundaries[:]


#     for i in range(diffPercentage.shape[0]):
#         for j in range(diffPercentage.shape[1]):
#             if diffPercentage[i][j] > 0:
#                 penalties[i][j] = inverseDistrib[minState + math.floor
#                                                   (diffPercentage[i][j] * overUtilVal)]
#             else:
#                 penalties[i][j] = inverseDistrib[minState + math.floor
#                                                   (diffPercentage[i][j] * underUtilVal)]

#     sumOfPenalty = 0
#     for i in range(predictionIndex.shape[0]):
#         penalties[i] = penalties[i] / np.sum(penalties[i])
#         sumOfPenalty += penalties[i][predictionIndex[i]]

#     return sumOfPenalty

def testAccuracy(predictedLables, trueLables):
    import sys
    np.set_printoptions(threshold=sys.maxsize)
    correctLableIndex = np.argmax(trueLables, 1)
    predictionIndex = np.argmax(predictedLables, 1)
    errors = [0 for i in range(trueLables.shape[1])]
    corrects = [0 for i in range(trueLables.shape[1])]
    for i in range(len(correctLableIndex)):
        if correctLableIndex[i] != predictionIndex[i]:
            errors[correctLableIndex[i]] += 1
            corrects[predictionIndex[i]] += 1
    print("errors: ", errors)
    print("corrects: ", corrects)
    acc = np.float64(np.sum(correctLableIndex == predictionIndex)/predictedLables.shape[0])
    # wrongPred = np.where(predictionIndex != correctLableIndex)
    # print(predictionIndex[wrongPred])
    # print(correctLableIndex[wrongPred])
    return acc
            

In [94]:
tensorFlowLossFunction(aa, XArraysForLearning, YArraysForLearning, XArraysForTesting, YArraysForTesting, boundaries)

Initialized
for epoch and loss: 0 51.31463180946199
0.703021523178808
for epoch and loss: 1 41.318605580866745
0.761692880794702
for epoch and loss: 2 40.75686353721363
0.7624689569536424
for epoch and loss: 3 40.50218301103603
0.7633485099337748


KeyboardInterrupt: 

In [182]:
# cuTrans = processData.markovianTransitionMatrixDegree1(data, 255, "CU")
# normalizedCuTrans = processData.normalizingTransMatrix(cuTrans)
reload(oldLumping)

for i in range(1):
    percentageMatrix_list, irreducible_matrix = preparingMatrixForLumping(normalizedCuTrans[32])
    result = oldLumping.lumping(irreducible_matrix, percentageMatrix_list, False)

0.99999994
1.0000001
0.99999994
0.9999999
0.99999994
0.99999994
1.0000001
1.0000001
1.0000001
we have these many sectors to check:  337462


In [183]:
result[0]

(1.0,
 50.422607421875,
 array([[0.16216216, 0.        , 0.        , 0.00865801, 0.        ,
         0.        ],
        [0.0053135 , 0.47821467, 0.03389831, 0.01184211, 0.0042508 ,
         0.        ],
        [0.00321543, 0.0659164 , 0.53432836, 0.06467662, 0.0079602 ,
         0.        ],
        [0.        , 0.04635762, 0.24107143, 0.42655936, 0.02419355,
         0.        ],
        [0.        , 0.1025641 , 0.07142857, 0.        , 0.09090909,
         0.        ],
        [0.        , 0.        , 0.        , 0.        , 0.        ,
         0.        ]]),
 0,
 array([[0.83333333, 0.74458874, 0.3027027 , 0.16666667, 0.01621622,
         0.01298701],
        [0.12888889, 0.8354143 , 0.4272051 , 0.08076514, 0.01842105,
         0.00610376],
        [0.01094527, 0.37810945, 0.67352941, 0.32958199, 0.02830189,
         0.00425985],
        [0.01796407, 0.14285714, 0.47516556, 0.58128079, 0.11111111,
         0.03076923],
        [0.14285714, 0.28571429, 0.5       , 0.47368421, 0.3

In [130]:
minDegree = np.inf
for i in range(len(result)):
    if result[i][0] < minDegree:
        minDegree = result[i][0]

arrs = []
for i in range(len(result)):   
    if result[i][0] == minDegree:
        arrs.append(result[i])

In [124]:
arrs[0]

(0.8,
 40.848388671875,
 array([[0.471     , 0.02164502, 0.        , 0.        , 0.        ,
         0.        ],
        [0.12748344, 0.54313725, 0.01470588, 0.        , 0.        ,
         0.        ],
        [0.17647059, 0.46666667, 0.10769231, 0.        , 0.        ,
         0.        ],
        [0.1       , 0.25      , 0.        , 0.09090909, 0.        ,
         0.        ],
        [0.2       , 0.        , 0.        , 0.        , 0.        ,
         0.        ],
        [0.        , 0.        , 0.        , 0.14285714, 0.14285714,
         0.        ]]),
 0,
 array([[0.471     , 0.02164502, 0.        , 0.        , 0.        ,
         0.        ],
        [0.12748344, 0.54313725, 0.01470588, 0.        , 0.        ,
         0.        ],
        [0.17647059, 0.46666667, 0.10769231, 0.        , 0.        ,
         0.        ],
        [0.1       , 0.25      , 0.        , 0.09090909, 0.        ,
         0.        ],
        [0.2       , 0.        , 0.        , 0.        , 0. 

In [257]:
tensorFlowLossNN(x[0][2], XArraysForLearning, YArraysForLearning, XArraysForTesting, YArraysForTesting, boundaries)

<tf.Variable 'Variable_2:0' shape=(6, 6) dtype=float32_ref>
[[0.9560636  0.04393635 0.         0.         0.         0.        ]
 [0.18601853 0.79252326 0.02145821 0.         0.         0.        ]
 [0.23503415 0.62153476 0.1434311  0.         0.         0.        ]
 [0.22680412 0.5670103  0.         0.20618556 0.         0.        ]
 [1.         0.         0.         0.         0.         0.        ]
 [0.         0.         0.         0.5        0.5        0.        ]]
Initialized
[35, 23, 0, 2, 0, 0]
[0, 1, 0, 0, 59, 0]
[40, 18, 1, 1, 0, 0]
[0, 0, 0, 0, 60, 0]
[34, 21, 1, 1, 0, 0]
[0, 1, 0, 0, 56, 0]
[42, 16, 0, 3, 0, 0]
[0, 1, 0, 0, 60, 0]
[35, 23, 2, 0, 0, 1]
[0, 1, 0, 0, 60, 0]
[36, 22, 0, 1, 0, 1]
[0, 0, 0, 0, 60, 0]
[29, 23, 1, 1, 0, 0]
[0, 1, 0, 0, 53, 0]
[40, 19, 2, 3, 0, 0]
[1, 2, 0, 0, 61, 0]
[40, 14, 4, 1, 0, 0]
[1, 2, 0, 0, 56, 0]
[39, 21, 1, 1, 0, 0]
[0, 1, 0, 0, 61, 0]
[38, 20, 6, 0, 0, 0]
[0, 1, 0, 0, 63, 0]
[34, 23, 2, 0, 0, 0]
[0, 1, 0, 0, 58, 0]
[39, 22, 1, 0, 0, 0]


[7, 14, 4, 0, 0, 0]
[16, 8, 0, 0, 1, 0]
[9, 14, 0, 1, 0, 1]
[16, 7, 0, 0, 2, 0]
[3, 11, 2, 0, 1, 0]
[13, 4, 0, 0, 0, 0]
[10, 16, 0, 1, 0, 0]
[16, 9, 0, 0, 2, 0]
[5, 10, 2, 2, 0, 0]
[13, 6, 0, 0, 0, 0]
[5, 13, 2, 1, 0, 0]
[15, 5, 0, 0, 1, 0]
[3, 13, 3, 0, 1, 0]
[16, 4, 0, 0, 0, 0]
[6, 13, 2, 0, 0, 0]
[14, 6, 0, 0, 1, 0]
[6, 7, 4, 1, 1, 0]
[9, 10, 0, 0, 0, 0]
[6, 10, 3, 0, 0, 0]
[10, 7, 0, 0, 2, 0]
[7, 11, 0, 0, 0, 0]
[11, 7, 0, 0, 0, 0]
[5, 19, 3, 0, 0, 0]
[20, 6, 0, 0, 1, 0]
[3, 12, 0, 1, 0, 0]
[12, 4, 0, 0, 0, 0]
[9, 11, 6, 0, 0, 1]
[17, 10, 0, 0, 0, 0]
[8, 9, 2, 1, 1, 0]
[11, 9, 0, 0, 1, 0]
[7, 10, 1, 1, 0, 0]
[10, 7, 0, 0, 2, 0]
[3, 13, 3, 1, 1, 0]
[16, 4, 0, 0, 1, 0]
[5, 10, 1, 0, 0, 0]
[11, 5, 0, 0, 0, 0]
[4, 15, 2, 1, 0, 0]
[18, 4, 0, 0, 0, 0]
[4, 13, 1, 0, 0, 0]
[13, 5, 0, 0, 0, 0]
[7, 9, 1, 0, 0, 0]
[9, 7, 0, 0, 1, 0]
[6, 17, 0, 1, 0, 0]
[17, 5, 0, 0, 2, 0]
[4, 9, 2, 1, 0, 0]
[10, 6, 0, 0, 0, 0]
[5, 19, 2, 0, 0, 0]
[18, 7, 0, 0, 1, 0]
[4, 14, 1, 1, 0, 0]
[16, 4, 0, 0, 0, 0]
[7,

[8, 6, 1, 0, 0, 0]
[7, 8, 0, 0, 0, 0]
[12, 3, 1, 0, 0, 0]
[3, 13, 0, 0, 0, 0]
[5, 7, 0, 3, 0, 0]
[8, 7, 0, 0, 0, 0]
[9, 2, 0, 0, 0, 1]
[3, 9, 0, 0, 0, 0]
[14, 4, 2, 2, 0, 0]
[7, 15, 0, 0, 0, 0]
[15, 6, 1, 0, 0, 0]
[7, 15, 0, 0, 0, 0]
[7, 5, 5, 1, 0, 0]
[6, 12, 0, 0, 0, 0]
[7, 8, 2, 2, 0, 0]
[8, 11, 0, 0, 0, 0]
[6, 7, 2, 2, 0, 0]
[8, 9, 0, 0, 0, 0]
[10, 5, 0, 0, 0, 0]
[4, 10, 0, 0, 1, 0]
[8, 2, 5, 0, 0, 0]
[3, 12, 0, 0, 0, 0]
[9, 5, 3, 0, 1, 0]
[6, 12, 0, 0, 0, 0]
[17, 4, 1, 0, 0, 0]
[4, 18, 0, 0, 0, 0]
[12, 7, 2, 2, 0, 0]
[8, 15, 0, 0, 0, 0]
[8, 5, 1, 0, 0, 0]
[5, 9, 0, 0, 0, 0]
[11, 3, 4, 0, 0, 0]
[2, 14, 0, 0, 2, 0]
[12, 2, 3, 1, 0, 0]
[4, 14, 0, 0, 0, 0]
[10, 5, 2, 0, 0, 0]
[5, 12, 0, 0, 0, 0]
[15, 6, 2, 2, 0, 0]
[8, 17, 0, 0, 0, 0]
[8, 1, 3, 2, 0, 0]
[2, 12, 0, 0, 0, 0]
[9, 4, 2, 0, 0, 0]
[5, 9, 0, 0, 1, 0]
[6, 4, 1, 0, 0, 0]
[4, 7, 0, 0, 0, 0]
[10, 3, 1, 1, 0, 0]
[4, 11, 0, 0, 0, 0]
[10, 6, 2, 0, 0, 0]
[6, 12, 0, 0, 0, 0]
[10, 5, 2, 1, 0, 0]
[5, 13, 0, 0, 0, 0]
[10, 6, 2, 0, 0, 0]

[6, 2, 0, 0, 0, 0]
[2, 6, 0, 0, 0, 0]
[14, 7, 1, 1, 0, 0]
[8, 15, 0, 0, 0, 0]
[13, 9, 0, 0, 0, 0]
[9, 13, 0, 0, 0, 0]
[9, 2, 4, 1, 0, 0]
[4, 12, 0, 0, 0, 0]
[3, 5, 2, 0, 0, 0]
[6, 4, 0, 0, 0, 0]
[15, 4, 3, 1, 0, 0]
[8, 15, 0, 0, 0, 0]
[15, 1, 3, 0, 0, 0]
[3, 16, 0, 0, 0, 0]
[8, 2, 2, 1, 0, 0]
[2, 11, 0, 0, 0, 0]
[10, 4, 2, 2, 0, 0]
[5, 13, 0, 0, 0, 0]
[15, 4, 1, 1, 0, 0]
[5, 16, 0, 0, 0, 0]
[16, 4, 4, 0, 0, 0]
[5, 19, 0, 0, 0, 0]
[8, 5, 0, 3, 0, 0]
[6, 10, 0, 0, 0, 0]
[10, 6, 1, 0, 0, 0]
[7, 10, 0, 0, 0, 0]
[9, 6, 1, 0, 0, 0]
[6, 10, 0, 0, 0, 0]
[7, 5, 0, 1, 0, 0]
[6, 7, 0, 0, 0, 0]
[12, 3, 2, 1, 0, 0]
[4, 14, 0, 0, 0, 0]
[10, 6, 3, 0, 0, 0]
[8, 11, 0, 0, 0, 0]
[10, 7, 0, 0, 0, 0]
[7, 10, 0, 0, 0, 0]
[14, 5, 2, 1, 1, 0]
[6, 17, 0, 0, 0, 0]
[13, 4, 0, 0, 0, 0]
[4, 13, 0, 0, 0, 0]
[13, 6, 1, 2, 0, 0]
[7, 15, 0, 0, 0, 0]
[11, 2, 1, 1, 1, 0]
[4, 12, 0, 0, 0, 0]
[6, 5, 2, 0, 0, 0]
[7, 6, 0, 0, 0, 0]
[11, 6, 3, 1, 0, 0]
[8, 13, 0, 0, 0, 0]
[10, 4, 3, 0, 0, 0]
[6, 11, 0, 0, 0, 0]
[10, 3, 2, 0

[5, 5, 3, 2, 1, 0]
[8, 8, 0, 0, 0, 0]
[9, 3, 2, 3, 0, 0]
[6, 11, 0, 0, 0, 0]
[6, 6, 4, 1, 0, 0]
[9, 8, 0, 0, 0, 0]
[5, 5, 0, 1, 0, 0]
[5, 6, 0, 0, 0, 0]
[11, 5, 0, 0, 0, 0]
[5, 11, 0, 0, 0, 0]
[12, 4, 4, 2, 1, 0]
[7, 16, 0, 0, 0, 0]
[8, 5, 2, 0, 1, 0]
[7, 9, 0, 0, 0, 0]
[11, 5, 1, 0, 0, 0]
[5, 12, 0, 0, 0, 0]
[11, 3, 0, 0, 0, 0]
[3, 11, 0, 0, 0, 0]
[8, 4, 1, 0, 1, 0]
[5, 9, 0, 0, 0, 0]
[10, 2, 1, 0, 0, 0]
[2, 11, 0, 0, 0, 0]
[10, 6, 1, 0, 0, 0]
[6, 11, 0, 0, 0, 0]
[8, 6, 0, 1, 0, 0]
[7, 8, 0, 0, 0, 0]
[8, 5, 4, 0, 0, 0]
[5, 12, 0, 0, 0, 0]
[10, 4, 1, 2, 0, 0]
[4, 13, 0, 0, 0, 0]
[10, 11, 0, 0, 0, 1]
[12, 10, 0, 0, 0, 0]
[14, 5, 2, 1, 0, 0]
[5, 17, 0, 0, 0, 0]
[12, 2, 3, 2, 0, 0]
[2, 17, 0, 0, 0, 0]
[7, 1, 3, 0, 0, 0]
[2, 9, 0, 0, 0, 0]
[8, 4, 2, 1, 0, 0]
[4, 11, 0, 0, 0, 0]
[7, 8, 2, 0, 0, 0]
[10, 7, 0, 0, 0, 0]
[12, 6, 3, 1, 0, 0]
[8, 14, 0, 0, 0, 0]
[12, 4, 2, 0, 0, 0]
[4, 14, 0, 0, 0, 0]
[5, 8, 3, 0, 1, 0]
[11, 6, 0, 0, 0, 0]
[11, 7, 2, 1, 0, 0]
[8, 13, 0, 0, 0, 0]
[11, 6, 1, 0, 0, 

...

[6, 4, 0, 0, 1, 0]
[5, 6, 0, 0, 0, 0]
[7, 10, 1, 0, 0, 0]
[10, 8, 0, 0, 0, 0]
[3, 3, 2, 1, 1, 0]
[6, 4, 0, 0, 0, 0]
[4, 3, 3, 3, 0, 0]
[5, 8, 0, 0, 0, 0]
[11, 8, 1, 0, 0, 0]
[9, 11, 0, 0, 0, 0]
[12, 3, 2, 1, 0, 0]
[3, 15, 0, 0, 0, 0]
[10, 3, 0, 0, 0, 0]
[3, 10, 0, 0, 0, 0]
[5, 4, 2, 0, 0, 0]
[4, 7, 0, 0, 0, 0]
[8, 7, 0, 0, 0, 0]
[7, 8, 0, 0, 0, 0]
[8, 6, 1, 0, 1, 0]
[7, 9, 0, 0, 0, 0]
[8, 3, 0, 1, 0, 0]
[4, 8, 0, 0, 0, 0]
[3, 6, 2, 1, 0, 0]
[8, 4, 0, 0, 0, 0]
[4, 4, 2, 1, 0, 0]
[5, 6, 0, 0, 0, 0]
[4, 6, 2, 1, 0, 0]
[7, 6, 0, 0, 0, 0]
[9, 6, 1, 0, 0, 0]
[7, 9, 0, 0, 0, 0]
[4, 5, 1, 1, 0, 0]
[5, 6, 0, 0, 0, 0]
[5, 6, 1, 0, 0, 0]
[6, 6, 0, 0, 0, 0]
[7, 9, 2, 0, 0, 0]
[10, 8, 0, 0, 0, 0]
[6, 6, 2, 1, 0, 0]
[7, 8, 0, 0, 0, 0]
[5, 12, 1, 2, 0, 0]
[15, 5, 0, 0, 0, 0]
[1, 9, 2, 2, 1, 0]
[11, 4, 0, 0, 0, 0]
[6, 11, 0, 1, 0, 0]
[12, 6, 0, 0, 0, 0]
[8, 4, 3, 0, 0, 0]
[5, 10, 0, 0, 0, 0]
[5, 8, 1, 1, 0, 0]
[9, 6, 0, 0, 0, 0]
[6, 6, 3, 0, 0, 0]
[7, 8, 0, 0, 0, 0]
[5, 4, 3, 1, 0, 0]
[5, 8, 0, 0, 0, 

[7, 6, 2, 0, 0, 0]
[7, 8, 0, 0, 0, 0]
[8, 7, 1, 0, 1, 0]
[8, 9, 0, 0, 0, 0]
[6, 6, 1, 3, 0, 0]
[8, 8, 0, 0, 0, 0]
[8, 6, 2, 2, 0, 0]
[7, 11, 0, 0, 0, 0]
[12, 1, 3, 0, 1, 0]
[2, 15, 0, 0, 0, 0]
[4, 5, 2, 0, 2, 0]
[7, 6, 0, 0, 0, 0]
[6, 9, 1, 0, 0, 0]
[10, 6, 0, 0, 0, 0]
[8, 5, 4, 2, 0, 0]
[7, 12, 0, 0, 0, 0]
[9, 7, 1, 0, 0, 0]
[7, 10, 0, 0, 0, 0]
[8, 4, 1, 4, 0, 0]
[6, 11, 0, 0, 0, 0]
[7, 2, 0, 1, 0, 0]
[2, 8, 0, 0, 0, 0]
[9, 8, 2, 1, 0, 0]
[8, 12, 0, 0, 0, 0]
[4, 3, 3, 0, 1, 0]
[6, 5, 0, 0, 0, 0]
[2, 5, 2, 1, 1, 0]
[8, 3, 0, 0, 0, 0]
[7, 4, 4, 0, 0, 0]
[4, 11, 0, 0, 0, 0]
[6, 8, 1, 1, 0, 0]
[9, 7, 0, 0, 0, 0]
[4, 6, 2, 0, 0, 0]
[6, 6, 0, 0, 0, 0]
[6, 4, 1, 0, 0, 0]
[5, 6, 0, 0, 0, 0]
[5, 6, 3, 1, 0, 0]
[8, 7, 0, 0, 0, 0]
[9, 6, 2, 0, 0, 0]
[7, 10, 0, 0, 0, 0]
[3, 5, 1, 0, 0, 0]
[5, 4, 0, 0, 0, 0]
[4, 9, 1, 0, 0, 0]
[10, 4, 0, 0, 0, 0]
[9, 4, 4, 2, 0, 0]
[7, 12, 0, 0, 0, 0]
[9, 8, 2, 0, 0, 0]
[8, 11, 0, 0, 0, 0]
[2, 3, 2, 0, 0, 0]
[4, 3, 0, 0, 0, 0]
[8, 6, 4, 0, 0, 0]
[8, 10, 0, 0, 0, 0

[6, 3, 2, 0, 0, 0]
[4, 7, 0, 0, 0, 0]
[7, 5, 3, 0, 0, 0]
[6, 9, 0, 0, 0, 0]
[9, 5, 1, 1, 2, 0]
[7, 11, 0, 0, 0, 0]
[3, 5, 1, 1, 0, 0]
[6, 4, 0, 0, 0, 0]
[7, 6, 0, 0, 0, 0]
[6, 7, 0, 0, 0, 0]
[6, 10, 3, 1, 0, 0]
[12, 8, 0, 0, 0, 0]
[6, 6, 0, 2, 0, 0]
[6, 8, 0, 0, 0, 0]
[4, 6, 2, 1, 0, 0]
[6, 7, 0, 0, 0, 0]
[10, 0, 2, 2, 0, 0]
[2, 12, 0, 0, 0, 0]
[7, 6, 0, 2, 0, 0]
[6, 9, 0, 0, 0, 0]
[7, 8, 1, 1, 0, 0]
[8, 9, 0, 0, 0, 0]
[10, 4, 1, 0, 0, 0]
[4, 11, 0, 0, 0, 0]
[6, 6, 3, 1, 0, 0]
[7, 9, 0, 0, 0, 0]
[8, 4, 1, 1, 0, 0]
[5, 9, 0, 0, 0, 0]
[2, 7, 0, 1, 0, 0]
[7, 3, 0, 0, 0, 0]
[7, 4, 2, 1, 0, 0]
[6, 8, 0, 0, 0, 0]
[3, 7, 2, 0, 0, 0]
[8, 4, 0, 0, 0, 0]
[4, 6, 4, 1, 0, 0]
[7, 8, 0, 0, 0, 0]
[9, 4, 1, 1, 0, 0]
[5, 10, 0, 0, 0, 0]
[6, 12, 2, 0, 0, 1]
[15, 6, 0, 0, 0, 0]
[6, 3, 1, 1, 0, 0]
[4, 7, 0, 0, 0, 0]
[6, 4, 0, 0, 0, 0]
[4, 6, 0, 0, 0, 0]
[10, 3, 2, 2, 0, 0]
[6, 11, 0, 0, 0, 0]
[4, 10, 0, 0, 0, 0]
[10, 4, 0, 0, 0, 0]
[3, 6, 0, 1, 0, 0]
[6, 4, 0, 0, 0, 0]
[2, 8, 0, 2, 1, 1]
[12, 2, 0, 0, 0, 

[10, 5, 3, 0, 0, 0]
[6, 12, 0, 0, 0, 0]
[9, 6, 2, 0, 0, 0]
[8, 9, 0, 0, 0, 0]
[5, 3, 4, 0, 0, 0]
[4, 8, 0, 0, 0, 0]
[5, 2, 2, 1, 0, 0]
[4, 6, 0, 0, 0, 0]
[9, 2, 3, 0, 0, 0]
[4, 10, 0, 0, 0, 0]
[6, 3, 1, 2, 0, 0]
[4, 8, 0, 0, 0, 0]
[8, 4, 2, 1, 0, 0]
[6, 9, 0, 0, 0, 0]
[7, 5, 2, 1, 0, 0]
[6, 9, 0, 0, 0, 0]
for epoch and loss: 64 0.64888424
0.7677462748344371
[547, 425, 115, 56, 15, 5]
[485, 678, 0, 0, 0, 0]
[5, 6, 2, 0, 0, 0]
[6, 7, 0, 0, 0, 0]
[9, 8, 3, 1, 0, 0]
[8, 13, 0, 0, 0, 0]
[7, 2, 0, 3, 0, 0]
[4, 8, 0, 0, 0, 0]
[8, 6, 1, 0, 1, 0]
[8, 8, 0, 0, 0, 0]
[8, 7, 1, 0, 0, 0]
[7, 9, 0, 0, 0, 0]
[8, 5, 3, 0, 0, 0]
[6, 10, 0, 0, 0, 0]
[6, 3, 0, 0, 0, 0]
[3, 6, 0, 0, 0, 0]
[9, 4, 2, 1, 0, 0]
[4, 12, 0, 0, 0, 0]
[8, 4, 2, 1, 0, 0]
[6, 9, 0, 0, 0, 0]
[6, 3, 3, 1, 0, 0]
[5, 8, 0, 0, 0, 0]
[8, 5, 1, 0, 0, 0]
[5, 9, 0, 0, 0, 0]
[9, 7, 0, 2, 0, 0]
[9, 9, 0, 0, 0, 0]
[5, 11, 1, 0, 0, 0]
[11, 6, 0, 0, 0, 0]
[3, 10, 0, 1, 0, 0]
[10, 4, 0, 0, 0, 0]
[7, 8, 0, 0, 0, 0]
[8, 7, 0, 0, 0, 0]
[5, 8, 2, 3, 

Penalty Value: 198.255
accuracy Result is:  0.7627503613462729
[[ 0.60694826  0.64919525  0.37588078  0.39138392  0.01260392 -0.25879407]
 [-0.02963072  0.5998159   0.2772051   0.32944733 -0.04735058  0.01278898]
 [ 0.05142     0.2763696   0.34926036  0.16262618  0.2940651   0.28894457]
 [ 0.30334765  0.8680408   0.39889026 -0.0509581  -0.41269374 -0.6773939 ]
 [ 1.0685188   0.65900075  0.2392491   0.03139436 -0.6993385  -0.06732972]
 [-0.17501187  0.40555373  0.47753292  0.05284265  0.37435597  0.48823148]]


In [253]:
x[0][2]

array([[0.95606365, 0.04393635, 0.        , 0.        , 0.        ,
        0.        ],
       [0.18601853, 0.79252326, 0.02145821, 0.        , 0.        ,
        0.        ],
       [0.23503415, 0.62153475, 0.1434311 , 0.        , 0.        ,
        0.        ],
       [0.22680412, 0.56701031, 0.        , 0.20618557, 0.        ,
        0.        ],
       [1.        , 0.        , 0.        , 0.        , 0.        ,
        0.        ],
       [0.        , 0.        , 0.        , 0.5       , 0.5       ,
        0.        ]])

In [250]:
x = normalLumps[32]
for i in range(x[0][2].shape[0]):
    x[0][2][i] = x[0][2][i]/np.sum(x[0][2][i])
print(x)
abs(pysal.spatial_dynamics.ergodic.steady_state(x[0][2]))

[(0.8, 40.607666015625, array([[0.95606365, 0.04393635, 0.        , 0.        , 0.        ,
        0.        ],
       [0.18601853, 0.79252326, 0.02145821, 0.        , 0.        ,
        0.        ],
       [0.23503415, 0.62153475, 0.1434311 , 0.        , 0.        ,
        0.        ],
       [0.22680412, 0.56701031, 0.        , 0.20618557, 0.        ,
        0.        ],
       [1.        , 0.        , 0.        , 0.        , 0.        ,
        0.        ],
       [0.        , 0.        , 0.        , 0.5       , 0.5       ,
        0.        ]]), [0, 19, 41, 53, 72, 83, 86])]


array([0.80992508, 0.18542966, 0.00464526, 0.        , 0.        ,
       0.        ])

In [229]:
normalLumps[31]

[(1.0,
  42.135498046875,
  array([[0.2       , 0.4       , 0.        , 0.        , 0.        ,
          0.        ],
         [0.00173913, 0.71039604, 0.02934537, 0.00410256, 0.        ,
          0.        ],
         [0.        , 0.275     , 0.34571429, 0.00478469, 0.        ,
          0.        ],
         [0.        , 0.30769231, 0.13636364, 0.11764706, 0.        ,
          0.        ],
         [0.        , 0.        , 0.11111111, 0.        , 0.        ,
          0.        ],
         [0.        , 0.        , 0.        , 0.        , 0.        ,
          0.        ]]),
  [0, 6, 31, 55, 71, 82, 90])]

col1  time    CU  CU/255  timeIndex  weekDay   day  corr1  corr2  \
0        True  True  True    True       True     True  True   True   True   
1        True  True  True    True       True     True  True   True   True   
2        True  True  True    True       True     True  True   True   True   
3        True  True  True    True       True     True  True   True   True   
4        True  True  True    True       True     True  True   True   True   
5        True  True  True    True       True     True  True   True   True   
6        True  True  True    True       True     True  True   True   True   
7        True  True  True    True       True     True  True   True   True   
8        True  True  True    True       True     True  True   True   True   
9        True  True  True    True       True     True  True   True   True   
10       True  True  True    True       True     True  True   True   True   
11       True  True  True    True       True     True  True   True   True   
12       True  True  True    True       True     True  True   True   True   
13       True  True  True    True       True     True  True   True   True   
14       True  True  True    True       True     True  True   True   True   
15       True  True  True    True       True     True  True   True   True   
16       True  True  True    True       True     True  True   True   True   
17       True  True  True    True       True     True  True   True   True   
18       True  True  True    True       True     True  True   True   True   
19       True  True  True    True       True     True  True   True   True   
20       True  True  True    True       True     True  True   True   True   
21       True  True  True    True       True     True  True   True   True   
22       True  True  True    True       True     True  True   True   True   
23       True  True  True    True       True     True  True   True   True   
24       True  True  True    True       True     True  True   True   True   
25       True  True  True    True       True     True  True   True   True   
26       True  True  True    True       True     True  True   True   True   
27       True  True  True    True       True     True  True   True   True   
28       True  True  True    True       True     True  True   True   True   
29       True  True  True    True       True     True  True   True   True   
...       ...   ...   ...     ...        ...      ...   ...    ...    ...   
1562706  True  True  True    True       True     True  True   True   True   
1562707  True  True  True    True       True     True  True   True   True   
1562708  True  True  True    True       True     True  True   True   True   
1562709  True  True  True    True       True     True  True   True   True   
1562710  True  True  True    True       True     True  True   True   True   
1562711  True  True  True    True       True     True  True   True   True   
1562712  True  True  True    True       True     True  True   True   True   
1562713  True  True  True    True       True     True  True   True   True   
1562714  True  True  True    True       True     True  True   True   True   
1562715  True  True  True    True       True     True  True   True   True   
1562716  True  True  True    True       True     True  True   True   True   
1562717  True  True  True    True       True     True  True   True   True   
1562718  True  True  True    True       True     True  True   True   True   
1562719  True  True  True    True       True     True  True   True   True   
1562720  True  True  True    True       True     True  True   True   True   
1562721  True  True  True    True       True     True  True   True   True   
1562722  True  True  True    True       True     True  True   True   True   
1562723  True  True  True    True       True     True  True   True   True   
1562724  True  True  True    True       True     True  True   True   True   
1562725  True  True  True    True       True     True  True   True   True   
15627

In [ ]:
uniqueDays = []
uniqueDays.extend(data.apply(lambda x: x["day"] if x["day"] not in uniqueDays else np.inf, axis = 1))
uniqueDays = list(set(uniqueDays))
shuffle(uniqueDays)

In [ ]:
days30 = uniqueDays[0:30]
data_within_30Days = data.loc[data["day"].isin(days30)]

In [ ]:

# data_within_30Days = data.loc[data["day"] <= 30]

numberOfStates = 255
cuTrans_30Days = processData.markovianTransitionMatrixDegree1(data_within_30Days, numberOfStates, "CU")
normalizedCuTrans_30Days = processData.normalizingTransMatrix(cuTrans_30Days)

In [6]:
# uniqueDays = []
# uniqueDays.extend(data.apply(lambda x: x["day"] if x["day"] not in uniqueDays else np.inf, axis = 1))

# uniqueDays = list(set(uniqueDays))
# # print(type(uniqueDays))
# print(uniqueDays)
from scipy import signal
pd.options.mode.chained_assignment = None
steadyState_30days = np.zeros(shape=(normalizedCuTrans_30Days.shape[0],
                                     normalizedCuTrans_30Days.shape[1]))

x = data.copy()

data.head()

[0, 1, 2, 3, 4, 7, 8, 9, 10, 11, 14, 15, 16, 17, 18, 21, 22, 23, 24, 25, 28, 29, 30, 31, 32, 35, 36, 37, 141, 146, 147, 148, 149, 150, 153, 154, 160, 161, 162, 163, 164, 167, 168, 177, 178, 182, 183, 184, 185, 188, 189, 190, 191, 192, 195, 196, 197, 198, 199, 201, 202, 203, 204, 205, 208, 209, 210, 211, 212, 215, 216, 217, 218, 219, 222, 223, 224, 225, 236, 237, 238, 239, 240, 243, 244, 245, 246, 247, 250, 251, 252, 253, 254, 257, 258, 259, 260, 264]


col1                time  CU    CU/255  timeIndex  weekDay  day
0     0 2018-11-12 19:01:32  45  0.176471         38        0    0
1     1 2018-11-12 19:01:38  45  0.176471         38        0    0
2     2 2018-11-12 19:01:44  51  0.200000         38        0    0
3     3 2018-11-12 19:01:50  53  0.207843         38        0    0
4     4 2018-11-12 19:01:56  45  0.176471         38        0    0

In [20]:
for i in range(normalizedCuTrans_30Days.shape[0]):
    steadyState_30days[i] = abs(pysal.spatial_dynamics.ergodic.steady_state(normalizedCuTrans_30Days[i]))

In [23]:
data = x.copy()

In [24]:
for dayNumber in uniqueDays:
    print(dayNumber)
    if dayNumber <= 30 or dayNumber >= 201:
        continue
    for timeIndex in range(max(data["timeIndex"]) + 1):
        oneIndexData = data.loc[(data["day"] == dayNumber) & (data["timeIndex"] == timeIndex)]
        if len(oneIndexData) == 0:
            continue
        indices = list(data["col1"].loc[(data["day"] == dayNumber) & (data["timeIndex"] == timeIndex)])
        oneIndexTrans = processData.markovianTransitionMatrixDegree1(oneIndexData, numberOfStates, "CU")
        oneIndexTrans = oneIndexTrans[-1]

        sum = 0
        for j in range(oneIndexTrans.shape[0]):
            sum = np.sum(oneIndexTrans[j])
            if sum != 0:
                oneIndexTrans[j] = oneIndexTrans[j]/sum

        oneIndexTrans = processData.normalizingTransMatrix(oneIndexTrans)

        steadyState = abs(pysal.spatial_dynamics.ergodic.steady_state(oneIndexTrans))
        correlationDistance = np.zeros(shape=(max(data["timeIndex"]) + 1, 1))
        for i in range(steadyState_30days.shape[0]):
            steadyState_30days[i] = (steadyState_30days[i] - np.mean(
                steadyState_30days[i])) / (np.std(steadyState_30days[i]) * len(steadyState_30days[i]))
            
            steadyState = (steadyState - np.mean(steadyState)) / (np.std(steadyState))
            correlationDistance[i] = signal.correlate(steadyState_30days[i],steadyState, mode="valid")

        # print(timeIndex)
        # print(cosineDistance)
        if np.argmax(correlationDistance) >= 0.98:
            data["timeIndex"].loc[(data["col1"] >= indices[0]) & (
                data["col1"] <= indices[-1])] = np.argmax(correlationDistance)

        else:
            print(np.max(correlationDistance), np.argmax(correlationDistance), max(data["timeIndex"]))
            data["timeIndex"].loc[(data["col1"] >= indices[0]) & (
                data["col1"] <= indices[-1])] = max(data["timeIndex"] + 1)

0
1
2
3
4
7
8
9
10
11
14
15
16
17
18
21
22
23
24
25
28
29
30
31
32
35
36
37
141
146
147
148
149
150
153
154
160
161
162
163
164
167
168
177
178
182
183
184
185
188
189
190
191
192
195
196
197
198
199
201
202
203
204
205
208
209
210
211
212
215
216
217
218
219
222
223
224
225
236
237
238
239
240
243
244
245
246
247
250
251
252
253
254
257
258
259
260
264


In [13]:
max(data["timeIndex"])

47

In [26]:
for i in range(max(data["timeIndex"]) + 1):
    print(i)
    extra = data.loc[(data["day"] <= 201) & (data["timeIndex"] == i)].copy()
    print(len(extra))

0
6297
1
8980
2
6737
3
83522
4
44309
5
35237
6
21499
7
48948
8
7601
9
6267
10
6410
11
7244
12
6436
13
6397
14
6294
15
8401
16
7577
17
7730
18
7045
19
7130
20
6504
21
15787
22
31911
23
6534
24
6576
25
6434
26
6532
27
7860
28
6428
29
9591
30
6517
31
6537
32
6512
33
6542
34
6517
35
6478
36
6494
37
6497
38
47039
39
48047
40
42008
41
8073
42
16656
43
6708
44
6938
45
6702
46
6689
47
7450


In [27]:
data_within_201 = data.loc[data["day"] <= 201]

numberOfStates = 255
cuTrans_201 = processData.markovianTransitionMatrixDegree1(data_within_201, numberOfStates, "CU")
normalizedCuTrans_201 = processData.normalizingTransMatrix(cuTrans_201)

In [55]:
for i in range(1):
    percentageMatrix_list, irreducible_matrix = preparingMatrixForLumping(normalizedCuTrans_201[29])
    result = oldLumping.lumping(irreducible_matrix, percentageMatrix_list, False)
#     nameResult = "/home/sepehr/thesis/APDataML/pickles/6normal_correlated_lumping_result2_" + str(i) + ".pickle"
#     with open(nameResult, 'wb') as handle:
#         pickle.dump(result, handle)
#     namePercent = "/home/sepehr/thesis/APDataML/pickles/6normal_correlated_lumping_percentage2_" + str(i) + ".pickle"
#     with open(namePercent, 'wb') as handle:
#         pickle.dump(percentageMatrix_list, handle)

0.99999994
0.99999994
0.99999994
1.0000001
0.99999994
0.99999994
1.0000001
we have these many sectors to check:  366134


In [56]:
candidateResult = []
minDegree = np.inf        
for i in range(len(result)):
    if result[i][0] < minDegree:
        minDegree = result[i][0]

minError = np.inf
for i in range(len(result)):
    if result[i][0] == minDegree and result[i][1] < minError:
        minError = result[i][1]

for i in range(len(result)):
    if result[i][0] == minDegree and result[i][1] == minError:
        candidateResult.append(result[i])

In [57]:
for i in range(len(candidateResult)):
    for x in range(len(candidateResult[i][3])):
        candidateResult[i][3][x] += 1

In [58]:
boundaries = np.array([])
for i in range(1, len(candidateResult[0][3]) - 1):
    bound = candidateResult[0][3][i]
    counter = 0
    for j in range(len(percentageMatrix_list)):
        if percentageMatrix_list[j][2] == False:
            counter += 1
        if counter == bound:
            boundaries = np.append(boundaries, percentageMatrix_list[j][1])
            break
boundaries = np.append(boundaries,100)

In [59]:
XArraysForLearning, YArraysForLearning, XArraysForTesting, YArraysForTesting, boundaries = simpleLogisticRegression(data_within_201, 20, 30, boundaries)
tensorFlowLossFunction(XArraysForLearning, YArraysForLearning, XArraysForTesting, YArraysForTesting, boundaries)

start training set generation
5203
Testing
length of test is:  1301
Initialized
Penalty Value: 10.044
accuracy Result is:  0.9338970023059185


In [51]:
data_within_201 = data.loc[data["day"] <= 201]

In [49]:
arrExtra = [0]
def particling(x):
    if (x["col1"] - 1 not in data["col1"]) or (x["col1"] - 1 < 0):
        arrExtra[0] = x["time"]
        return 0

    elif x["timeIndex"] != data["timeIndex"][x["col1"] - 1]:
        arrExtra[0] = x["time"]
        return 0

    else:
        return ((x["time"] - arrExtra[0]).seconds)/6

data["periodParticle"] = data.apply(lambda x: particling(x), axis = 1) #numbering each 6 seconds in the dataFrame
